In [1]:
import pandas as pd
import numpy as np
import pickle

from sklearn.linear_model import LinearRegression
from sklearn.linear_model import LogisticRegression
from sklearn.tree import DecisionTreeClassifier
from sklearn.ensemble import RandomForestClassifier
from sklearn.model_selection import train_test_split
from sklearn import metrics
from sklearn.model_selection import cross_validate
from sklearn.model_selection import cross_val_score
from sklearn.tree import export_graphviz
from sklearn.neighbors import KNeighborsRegressor
from sklearn.neural_network import MLPRegressor
import matplotlib.pyplot as plt
%matplotlib inline

import warnings

In [2]:
#!/usr/bin/env python
# coding: utf-8

# ## Analysis of Random Sample of 1 million leavetimes merged with trips data

# In[2]:


df1 = pd.read_csv('../../data/leavetimes_trips_1e6.csv',sep=',')


# In[3]:


df1.head()

Unnamed: 0 DATASOURCE        DAYOFSERVICE   TRIPID  PROGRNUMBER  \
0           0         DB  25-AUG-18 00:00:00  7329034           32   
1           1         DB  31-MAY-18 00:00:00  6847697           13   
2           2         DB  26-MAY-18 00:00:00  6780534           14   
3           3         DB  23-APR-18 00:00:00  6635422            7   
4           4         DB  06-APR-18 00:00:00  6606411           33   

   STOPPOINTID  PLANNEDTIME_ARR  PLANNEDTIME_DEP  ACTUALTIME_ARR  \
0          609            46010            46010           45900   
1          847            33619            33619           33604   
2         4758            57703            57703           57898   
3         7030            27325            27325           27474   
4         1453            85482            85482           86219   

   ACTUALTIME_DEP  ...  NOTE_x  LINEID  ROUTEID  DIRECTION   BASIN  TENDERLOT  \
0           45900  ...     NaN     29A   29A_15          2  BasDef        NaN   
1           33616  ...     NaN     145  145_102          1  BasDef        NaN   
2           57917  ...     NaN      49    49_28          2  BasDef        NaN   
3           27511  ...     NaN     39A   39A_43          2  BasDef        NaN   
4           86219  ...     NaN     123   123_36          2  BasDef        NaN   

   SUPPRESSED_y JUSTIFICATIONID_y        LASTUPDATE_y     NOTE_y  
0           NaN               NaN  03-SEP-18 10:39:32  ,2478282,  
1           NaN               NaN  14-JUN-18 14:04:06  ,3272689,  
2           NaN               NaN  14-JUN-18 13:12:56  ,1726258,  
3           NaN               NaN  13-JUN-18 08:27:05  ,2424410,  
4           NaN               NaN  18-APR-18 10:49:06  ,3222191,  

[5 rows x 28 columns]

In [3]:

# In[4]:


df1.drop('Unnamed: 0',axis=1,inplace=True)


# In[5]:


# dtypes 
df1['DATASOURCE'] = df1['DATASOURCE'].astype('category')
df1['DAYOFSERVICE'] = df1['DAYOFSERVICE'].astype('datetime64')
df1['TRIPID'] = df1['TRIPID'].astype('object')
df1['PROGRNUMBER'] = df1['PROGRNUMBER'].astype('category')
df1['STOPPOINTID'] = df1['STOPPOINTID'].astype('category')
df1['VEHICLEID'] = df1['VEHICLEID'].astype('object')
df1['SUPPRESSED_x'] = df1['SUPPRESSED_x'].astype('category')
df1['JUSTIFICATIONID_x'] = df1['JUSTIFICATIONID_x'].astype('category')
df1['DIRECTION'] = df1['DIRECTION'].astype('category')
df1['SUPPRESSED_y'] = df1['SUPPRESSED_y'].astype('category')
df1['JUSTIFICATIONID_y'] = df1['JUSTIFICATIONID_y'].astype('category')
df1['TENDERLOT'] = df1['TENDERLOT'].astype('category')
df1['NOTE_x'] = df1['NOTE_x'].astype('category')
df1['PASSENGERS'] = df1['PASSENGERS'].astype('category')
df1['PASSENGERSIN'] = df1['PASSENGERSIN'].astype('category')
df1['PASSENGERSOUT'] = df1['PASSENGERSOUT'].astype('category')
df1['DISTANCE'] = df1['DISTANCE'].astype('category')
df1['NOTE_y'] = df1['DISTANCE'].astype('category')
df1['LASTUPDATE_x'] = df1['LASTUPDATE_x'].astype('datetime64')
df1['LASTUPDATE_y'] = df1['LASTUPDATE_y'].astype('datetime64')
df1['BASIN'] = df1['BASIN'].astype('category')
df1['LINEID'] = df1['LINEID'].astype('category')


# In[6]:


df1.dtypes


# In[7]:


categorical_columns = df1.select_dtypes('category').columns
numerical_columns = df1.select_dtypes('int64','float64').columns
object_columns = df1.select_dtypes('object').columns


# In[8]:


df1[categorical_columns].describe().T


# In[9]:


df1.drop(['PASSENGERS','PASSENGERSIN','PASSENGERSOUT','DISTANCE','NOTE_x'],axis=1,inplace=True)


# In[10]:


categorical_columns = df1.select_dtypes('category').columns


# In[11]:


df1[categorical_columns].describe().T


# In[12]:


df1.drop(['TENDERLOT','NOTE_y','BASIN','SUPPRESSED_y','JUSTIFICATIONID_y'],axis=1,inplace=True)


# In[13]:


categorical_columns = df1.select_dtypes('category').columns


# In[14]:


df1[categorical_columns].describe().T


# In[15]:


df1.head()


# In[16]:


df1_simple = df1.drop([
    'LASTUPDATE_y',
    'ROUTEID',
    'LASTUPDATE_x',
    'JUSTIFICATIONID_x',
    'SUPPRESSED_x',
    'ACTUALTIME_DEP',
    'VEHICLEID',
    'PLANNEDTIME_DEP'
],axis=1)

# df1_simple.drop(['PROGNUMBER','TRIPID'],axis=1,inplace=True)

# In[17]:


df1_simple.head()


# In[18]:


df1_simple.dtypes


# In[24]:


df1_simple['MONTH'] = df1_simple['DAYOFSERVICE'].dt.month.astype('category')
df1_simple['WEEKDAY'] = df1_simple['DAYOFSERVICE'].dt.weekday.astype('category')
# df1_simple.drop('DAYOFSERVICE',axis=1,inplace=True)


# In[25]:


df1_simple.head()


# In[26]:


df1_simple.dtypes


# In[ ]:


DATASOURCE               category
DAYOFSERVICE       datetime64[ns]
TRIPID                     object
PROGRNUMBER              category
STOPPOINTID              category
PLANNEDTIME_ARR             int64
ACTUALTIME_ARR              int64
LINEID                   category
DIRECTION                category
MONTH                    category
WEEKDAY                  category
dtype: object

In [4]:
df1_simple.head()

DATASOURCE DAYOFSERVICE   TRIPID PROGRNUMBER STOPPOINTID  PLANNEDTIME_ARR  \
0         DB   2018-08-25  7329034          32         609            46010   
1         DB   2018-05-31  6847697          13         847            33619   
2         DB   2018-05-26  6780534          14        4758            57703   
3         DB   2018-04-23  6635422           7        7030            27325   
4         DB   2018-04-06  6606411          33        1453            85482   

   ACTUALTIME_ARR LINEID DIRECTION MONTH WEEKDAY  
0           45900    29A         2     8       5  
1           33604    145         1     5       3  
2           57898     49         2     5       5  
3           27474    39A         2     4       0  
4           86219    123         2     4       4

In [5]:
# df1_simple['ARR_DELTA'] = df1_simple['PLANNEDTIME_ARR'] - df1_simple['ACTUALTIME_ARR']
# df1_simple.drop('ACTUALTIME_ARR',axis=1,inplace=True)

In [6]:
df1_simple.head()

DATASOURCE DAYOFSERVICE   TRIPID PROGRNUMBER STOPPOINTID  PLANNEDTIME_ARR  \
0         DB   2018-08-25  7329034          32         609            46010   
1         DB   2018-05-31  6847697          13         847            33619   
2         DB   2018-05-26  6780534          14        4758            57703   
3         DB   2018-04-23  6635422           7        7030            27325   
4         DB   2018-04-06  6606411          33        1453            85482   

   ACTUALTIME_ARR LINEID DIRECTION MONTH WEEKDAY  
0           45900    29A         2     8       5  
1           33604    145         1     5       3  
2           57898     49         2     5       5  
3           27474    39A         2     4       0  
4           86219    123         2     4       4

In [7]:
categorical_columns = df1_simple.select_dtypes('category').columns
df1_simple[categorical_columns].describe().T

count unique   top     freq
DATASOURCE   1000000      1    DB  1000000
PROGRNUMBER  1000000    105    13    18239
STOPPOINTID  1000000   4730  1478     1777
LINEID       1000000    130    40    37314
DIRECTION    1000000      2     2   505863
MONTH        1000000     12     1    90097
WEEKDAY      1000000      7     1   163043

### 

## 1 bus route

route = '16'

df1_simple_1route = df1_simple[df1_simple['LINEID'] == route]

df1_simple_1route.shape[0]/130

df1_simple_1route[categorical_columns].describe().T

df1_simple_1route['lateness'] = df1_simple_1route['ACTUALTIME_ARR'] - df1_simple_1route['PLANNEDTIME_ARR']

df1_simple_1route.head()

hour = (df1_simple_1route['PLANNEDTIME_ARR']/(60*60)).astype('int64')
df1_simple_1route['Hour'] = hour
df1_simple_1route.groupby('Hour')['lateness'].mean().plot()
plt.ylabel('Lateness (s)')
plt.title('Average Lateness for 30,000 random %s arrivals'%route)
plt.savefig('%s_lateness.png'%route,dpi=720)

df1_simple_1route.drop('LINEID',axis=1,inplace=True)
df_rev1 = pd.get_dummies(df1_simple_1route)

continuous_columns = df_rev1.select_dtypes(include=['int64']).columns.tolist()
# remove the target "binary_outcome"
continuous_columns

categorical_columns = df_rev1.select_dtypes(include=['uint8']).columns.tolist()
categorical_columns

## Train-test Split

# y is the target
y = df_rev1["ACTUALTIME_ARR"]
# X is everything else
X = df_rev1.drop(["ACTUALTIME_ARR"],1)
# Split the dataset into two datasets: 70% training and 30% test
X_train, X_test, y_train, y_test = train_test_split(X, y, random_state=1,  test_size=0.3)

print("original range is: ",df_rev1.shape[0])
print("training range (70%):\t rows 0 to", round(X_train.shape[0]))
print("test range (30%): \t rows", round(X_train.shape[0]), "to", round(X_train.shape[0]) + X_test.shape[0])

# need to reset the index to allow contatenation with predicted values otherwise not joining on same index...
X_train.reset_index(drop=True, inplace=True)
y_train.reset_index(drop=True, inplace=True)
X_test.reset_index(drop=True, inplace=True)
y_test.reset_index(drop=True, inplace=True)
X_train.head(5)

## Linear Regression with 1 bus route

# Train aka fit, a model using all continuous and categorical features.
multiple_linreg = LinearRegression().fit(X_train, y_train)

# Print the weights learned for each feature.
print("\nFeatures are: \n", X_train.columns)
print("\nCoeficients are: \n", multiple_linreg.coef_)
print("\nIntercept is: \n", multiple_linreg.intercept_)
print("\nFeatures and coeficients: \n")#, list(zip(X_train.columns, multiple_linreg.coef_)))
for i in list(zip(X_train.columns,multiple_linreg.coef_)):
    print("{:e}".format(i[1]), i[0])

# calculate the prediction and threshold the value. If >= 0.5 its true
multiple_linreg_predictions_train = multiple_linreg.predict(X_train)
actual_vs_predicted_multiplelinreg = pd.concat([y_train, pd.DataFrame(multiple_linreg_predictions_train, columns=['Predicted'])], axis=1)

print("\nUnthresholded predictions with multiple linear regression: \n")
print(actual_vs_predicted_multiplelinreg.head(10))
print()

#This function is used repeatedly to compute all metrics
def printMetrics(testActualVal, predictions):
    #classification evaluation measures
    print('\n==============================================================================')
    print("MAE: ", metrics.mean_absolute_error(testActualVal, predictions))
    #print("MSE: ", metrics.mean_squared_error(testActualVal, predictions))
    print("RMSE: ", metrics.mean_squared_error(testActualVal, predictions)**0.5)
    print("R2: ", metrics.r2_score(testActualVal, predictions))

printMetrics(y_train, multiple_linreg_predictions_train)

# Predicted price on test set
test_predictions = multiple_linreg.predict(X_test)
print("Actual values of test:\n", y_test)
print("Predictions on test:", test_predictions)
printMetrics(y_test, test_predictions)

#Timetabled Arrival Time
printMetrics(y_test, X_test['PLANNEDTIME_ARR'])

## SVM with one route

from sklearn import svm

svr = svm.LinearSVR().fit(X_train,y_train)

# calculate the prediction and threshold the value. If >= 0.5 its true
svr_predictions_train = svr.predict(X_train)
actual_vs_predicted_svr = pd.concat([y_train, pd.DataFrame(svr_predictions_train, columns=['Predicted'])], axis=1)

print("\nUnthresholded predictions with svr: \n")
print(actual_vs_predicted_svr.head(10))
print()

printMetrics(y_train, svr_predictions_train)

## All Trips on 46A

df1_simple_1route.head()

TRIPIDs = df1_simple_1route['TRIPID'].unique()
# DAYS = df1_simple_1route['DAYOFSERVICE'].unique()
count = 0
for ID in TRIPIDs:
    DAYS = df1_simple_1route[df1_simple_1route['TRIPID'] == ID]['DAYOFSERVICE']
    for day in DAYS:
        print(day)
#         print(df1_simple[df1_simple['TRIPID'] == ID and df1_simple['DAYOFSERVICE'] == day].shape)


df1_simple_1route_1 = df1_simple_1route[df1_simple_1route['DIRECTION'] == 1]

df1_simple_1route_1.head()

df1_simple_1route_1.shape

## Trips Data Investigation

dftrips = pd.read_csv('../../data/rt_trips_DB_2018.txt',sep=';')

dftrips.head()

dftrips.drop(['TRIPID','DAYOFSERVICE','DATASOURCE','DAYOFSERVICE','BASIN','TENDERLOT','SUPPRESSED','JUSTIFICATIONID','LASTUPDATE','NOTE','ROUTEID'],axis=1,inplace=True)

dftrips.head()

dftrips.dropna(inplace=True)

dftrips.dtypes

dftrips['DIRECTION'] = dftrips['DIRECTION'].astype('category')
dftrips['LINEID'] = dftrips['LINEID'].astype('category')
dftrips['ACTUALTIME_ARR'] = dftrips['ACTUALTIME_ARR'].astype('int64')
dftrips['ACTUALTIME_DEP'] = dftrips['ACTUALTIME_DEP'].astype('int64')
dftrips['LINEID'] = dftrips['LINEID'].astype('category')

dftrips['TRIPLENGTH'] = dftrips['ACTUALTIME_ARR'] - dftrips['ACTUALTIME_DEP']

dftrips.head()

categorical_columns = dftrips.select_dtypes('category').columns
numerical_columns = dftrips.select_dtypes('int64').columns

dftrips.head()

dftrips[categorical_columns].describe().T

dftrips[numerical_columns].describe().T

dftrips[dftrips['TRIPLENGTH'] < 0].sort_values('ACTUALTIME_ARR',ascending=True)

dftrips = dftrips[dftrips['TRIPLENGTH'] > 0]

dftrips.drop(['ACTUALTIME_ARR','ACTUALTIME_DEP'],axis=1,inplace=True)

dftrips.head()

### Train/Test Split

dftrips_46A = dftrips[dftrips['LINEID'] == '46A'][dftrips['DIRECTION'] == 2].drop(['LINEID','DIRECTION'],axis=1)

df_rev1 = pd.get_dummies(dftrips_46A)

df_rev1.head()

# y is the target
y = df_rev1["TRIPLENGTH"]
# X is everything else
X = df_rev1.drop(["TRIPLENGTH"],1)
# Split the dataset into two datasets: 70% training and 30% test
X_train, X_test, y_train, y_test = train_test_split(X, y, random_state=1,  test_size=0.3)

print("original range is: ",df_rev1.shape[0])
print("training range (70%):\t rows 0 to", round(X_train.shape[0]))
print("test range (30%): \t rows", round(X_train.shape[0]), "to", round(X_train.shape[0]) + X_test.shape[0])

# need to reset the index to allow contatenation with predicted values otherwise not joining on same index...
X_train.reset_index(drop=True, inplace=True)
y_train.reset_index(drop=True, inplace=True)
X_test.reset_index(drop=True, inplace=True)
y_test.reset_index(drop=True, inplace=True)
X_train.head(5)

## Linear Regression with 1 bus route

# Train aka fit, a model using all continuous and categorical features.
multiple_linreg = LinearRegression().fit(X_train, y_train)

# Print the weights learned for each feature.
print("\nFeatures are: \n", X_train.columns)
print("\nCoeficients are: \n", multiple_linreg.coef_)
print("\nIntercept is: \n", multiple_linreg.intercept_)
print("\nFeatures and coeficients: \n")#, list(zip(X_train.columns, multiple_linreg.coef_)))
for i in list(zip(X_train.columns,multiple_linreg.coef_)):
    print("{:e}".format(i[1]), i[0])

# calculate the prediction and threshold the value. If >= 0.5 its true
multiple_linreg_predictions_train = multiple_linreg.predict(X_train)
actual_vs_predicted_multiplelinreg = pd.concat([y_train, pd.DataFrame(multiple_linreg_predictions_train, columns=['Predicted'])], axis=1)

print("\nUnthresholded predictions with multiple linear regression: \n")
print(actual_vs_predicted_multiplelinreg.head(10))
print()

#This function is used repeatedly to compute all metrics
def printMetrics(testActualVal, predictions):
    #classification evaluation measures
    print('\n==============================================================================')
    print("MAE: ", metrics.mean_absolute_error(testActualVal, predictions))
    #print("MSE: ", metrics.mean_squared_error(testActualVal, predictions))
    print("RMSE: ", metrics.mean_squared_error(testActualVal, predictions)**0.5)
    print("R2: ", metrics.r2_score(testActualVal, predictions))

printMetrics(y_train, multiple_linreg_predictions_train)

# Predicted price on test set
test_predictions = multiple_linreg.predict(X_test)
print("Actual values of test:\n", y_test)
print("Predictions on test:", test_predictions)
printMetrics(y_test, test_predictions)

#Timetabled Arrival Time
printMetrics(y_test, X_test['PLANNEDTIME_ARR'] - X_test['PLANNEDTIME_DEP'])

df_weather = pd.read_csv('../../data/historic_weather_data.csv')

df_weather.head()

df_weather.dtypes

df_weather.drop(['city_name','weather_icon','weather_description','sea_level','grnd_level','lon','lat','dt_iso','weather_id'],axis=1,inplace=True)

df_weather.dtypes

df_weather['timezone'] = df_weather['timezone'].astype('category')
df_weather['weather_main'] = df_weather['weather_main'].astype('category')

df_weather.dtypes

categorical_columns_w = df_weather.select_dtypes('category').columns
numerical_columns_w = df_weather.select_dtypes(['int64','float64']).columns

numerical_columns_w

# Prepare %missing column
category_columns_perc_missing  = 100 * (df_weather[categorical_columns_w].isnull().sum()/df_weather.shape[0])
#category_columns_perc_missing

# Store the values in a dataframe
df_category_perc_missing = pd.DataFrame(category_columns_perc_missing, columns=['%missing'])
df_category_perc_missing

# Prepare the cardinality column
category_columns_card = df_weather[categorical_columns_w].nunique()
# store the values in a dataframe
df_category_card = pd.DataFrame(category_columns_card, columns=['card'])
df_category_card

# Add missing values column
df_table_categ = df_weather[categorical_columns_w].describe().T
df_table_categ

#Combing the tables for data quality report table
df_category_columns_data_quality_report_table = pd.concat([df_table_categ, df_category_perc_missing, df_category_card], axis=1)
df_category_columns_data_quality_report_table

# Prepare %missing column
category_columns_perc_missing  = 100 * (df_weather[numerical_columns_w].isnull().sum()/df_weather.shape[0])
#category_columns_perc_missing

# Store the values in a dataframe
df_category_perc_missing = pd.DataFrame(category_columns_perc_missing, columns=['%missing'])
df_category_perc_missing

# Prepare the cardinality column
category_columns_card = df_weather[numerical_columns_w].nunique()
# store the values in a dataframe
df_category_card = pd.DataFrame(category_columns_card, columns=['card'])
df_category_card

# Add missing values column
df_table_categ = df_weather[numerical_columns_w].describe().T
df_table_categ

#Combing the tables for data quality report table
df_category_columns_data_quality_report_table = pd.concat([df_table_categ, df_category_perc_missing, df_category_card], axis=1)
df_category_columns_data_quality_report_table

#Drop columns with over 90% missing
df_weather.drop(['rain_1h','rain_3h','snow_1h','snow_3h'],axis=1,inplace=True)

df_weather.head()

df_weather_simple = df_weather.drop(['temp_min','temp_max','pressure','clouds_all','wind_speed','wind_deg'],axis=1)

df_weather_simple.head()

import datetime

df_weather_simple['date'] = pd.to_datetime(df_weather_simple['dt'], unit='s').dt.date
df_weather_simple['time'] = pd.to_datetime(df_weather_simple['dt'], unit='s').dt.time

df_weather_simple.head()

df_weather_simple.dtypes

## Add Trip info to Stop Info

dftrips.head()

dftrips = pd.read_csv('../../data/rt_trips_DB_2018.txt',sep=';')

dftrips.head()

dftrips.drop(['DATASOURCE','BASIN','TENDERLOT','SUPPRESSED','JUSTIFICATIONID','LASTUPDATE','NOTE','ROUTEID','DIRECTION'],axis=1,inplace=True)

dftrips.head()

df1_simple.head()

dftrips['DAYOFSERVICE'] = pd.to_datetime(dftrips['DAYOFSERVICE'])

df_merged = df1_simple.merge(dftrips,how='left',on=['DAYOFSERVICE','TRIPID'])

df_merged.head()

df_merged['TRIP_FRAC'] = (df_merged['ACTUALTIME_ARR_y'] - df_merged['ACTUALTIME_ARR_x'])/(df_merged['ACTUALTIME_ARR_y'] - df_merged['PLANNEDTIME_DEP'])

df_merged.head()

df_merged_46a_1 = df_merged[df_merged['LINEID_x']=='46A'][df_merged['DIRECTION_x'] == 1]
df_merged_46a_1.head()

df_merged_46a_1['PROGRNUMBER'] = df_merged_46a_1['PROGRNUMBER'].cat.remove_unused_categories()

df_merged_46a_1.groupby('PROGRNUMBER', as_index=False)['TRIP_FRAC'].mean()

import numpy as np

df_merged_46a_1.groupby('PROGRNUMBER', as_index=False)['TRIP_FRAC'].std()

df_merged_46a_1 = df_merged_46a_1.dropna()

df_merged_46a_1.groupby('PROGRNUMBER', as_index=False)['TRIP_FRAC'].apply(lambda x: x.sem())

## Multi-route Planning without Weather

In [8]:
df1 = pd.read_csv('../../data/leavetimes_trips_1e6.csv',sep=',')

df1.head()

Unnamed: 0 DATASOURCE        DAYOFSERVICE   TRIPID  PROGRNUMBER  \
0           0         DB  25-AUG-18 00:00:00  7329034           32   
1           1         DB  31-MAY-18 00:00:00  6847697           13   
2           2         DB  26-MAY-18 00:00:00  6780534           14   
3           3         DB  23-APR-18 00:00:00  6635422            7   
4           4         DB  06-APR-18 00:00:00  6606411           33   

   STOPPOINTID  PLANNEDTIME_ARR  PLANNEDTIME_DEP  ACTUALTIME_ARR  \
0          609            46010            46010           45900   
1          847            33619            33619           33604   
2         4758            57703            57703           57898   
3         7030            27325            27325           27474   
4         1453            85482            85482           86219   

   ACTUALTIME_DEP  ...  NOTE_x  LINEID  ROUTEID  DIRECTION   BASIN  TENDERLOT  \
0           45900  ...     NaN     29A   29A_15          2  BasDef        NaN   
1           33616  ...     NaN     145  145_102          1  BasDef        NaN   
2           57917  ...     NaN      49    49_28          2  BasDef        NaN   
3           27511  ...     NaN     39A   39A_43          2  BasDef        NaN   
4           86219  ...     NaN     123   123_36          2  BasDef        NaN   

   SUPPRESSED_y JUSTIFICATIONID_y        LASTUPDATE_y     NOTE_y  
0           NaN               NaN  03-SEP-18 10:39:32  ,2478282,  
1           NaN               NaN  14-JUN-18 14:04:06  ,3272689,  
2           NaN               NaN  14-JUN-18 13:12:56  ,1726258,  
3           NaN               NaN  13-JUN-18 08:27:05  ,2424410,  
4           NaN               NaN  18-APR-18 10:49:06  ,3222191,  

[5 rows x 28 columns]

In [9]:
df1.drop('Unnamed: 0',axis=1,inplace=True)

# dtypes 
df1['DATASOURCE'] = df1['DATASOURCE'].astype('category')
df1['DAYOFSERVICE'] = df1['DAYOFSERVICE'].astype('datetime64')
df1['TRIPID'] = df1['TRIPID'].astype('object')
df1['PROGRNUMBER'] = df1['PROGRNUMBER'].astype('category')
df1['STOPPOINTID'] = df1['STOPPOINTID'].astype('category')
df1['VEHICLEID'] = df1['VEHICLEID'].astype('object')
df1['SUPPRESSED_x'] = df1['SUPPRESSED_x'].astype('category')
df1['JUSTIFICATIONID_x'] = df1['JUSTIFICATIONID_x'].astype('category')
df1['DIRECTION'] = df1['DIRECTION'].astype('category')
df1['SUPPRESSED_y'] = df1['SUPPRESSED_y'].astype('category')
df1['JUSTIFICATIONID_y'] = df1['JUSTIFICATIONID_y'].astype('category')
df1['TENDERLOT'] = df1['TENDERLOT'].astype('category')
df1['NOTE_x'] = df1['NOTE_x'].astype('category')
df1['PASSENGERS'] = df1['PASSENGERS'].astype('category')
df1['PASSENGERSIN'] = df1['PASSENGERSIN'].astype('category')
df1['PASSENGERSOUT'] = df1['PASSENGERSOUT'].astype('category')
df1['DISTANCE'] = df1['DISTANCE'].astype('category')
df1['NOTE_y'] = df1['DISTANCE'].astype('category')
df1['LASTUPDATE_x'] = df1['LASTUPDATE_x'].astype('datetime64')
df1['LASTUPDATE_y'] = df1['LASTUPDATE_y'].astype('datetime64')
df1['BASIN'] = df1['BASIN'].astype('category')
df1['LINEID'] = df1['LINEID'].astype('category')

categorical_columns = df1.select_dtypes('category').columns
numerical_columns = df1.select_dtypes('int64','float64').columns
object_columns = df1.select_dtypes('object').columns

In [10]:
df1[categorical_columns].describe().T

count unique          top     freq
DATASOURCE         1000000      1           DB  1000000
PROGRNUMBER        1000000    105           13    18239
STOPPOINTID        1000000   4730         1478     1777
PASSENGERS               0      0          NaN      NaN
PASSENGERSIN             0      0          NaN      NaN
PASSENGERSOUT            0      0          NaN      NaN
DISTANCE                 0      0          NaN      NaN
SUPPRESSED_x          4986      2            0     3753
JUSTIFICATIONID_x     4985   3403  4.84981e+17       26
NOTE_x                   0      0          NaN      NaN
LINEID             1000000    130           40    37314
DIRECTION          1000000      2            2   505863
BASIN              1000000      1       BasDef  1000000
TENDERLOT                0      0          NaN      NaN
SUPPRESSED_y           556      1            0      556
JUSTIFICATIONID_y      555    470       291650        6
NOTE_y                   0      0          NaN      NaN

In [11]:
df1.drop(['PASSENGERS','PASSENGERSIN','PASSENGERSOUT','DISTANCE','NOTE_x'],axis=1,inplace=True)
df1.drop(['TENDERLOT','NOTE_y','BASIN','SUPPRESSED_y','JUSTIFICATIONID_y'],axis=1,inplace=True)

categorical_columns = df1.select_dtypes('category').columns

df1.head()


# In[16]:


df1_simple = df1.drop([
    'LASTUPDATE_y',
    'ROUTEID',
    'LASTUPDATE_x',
    'JUSTIFICATIONID_x',
    'SUPPRESSED_x',
    'ACTUALTIME_DEP',
    'VEHICLEID',
    'PLANNEDTIME_DEP'
],axis=1)

# df1_simple['MONTH'] = df1_simple['DAYOFSERVICE'].dt.month.astype('category')
# df1_simple['WEEKDAY'] = df1_simple['DAYOFSERVICE'].dt.weekday.astype('category')
# df1_simple.drop('DAYOFSERVICE',axis=1,inplace=True)

In [12]:
df1_simple.head()

DATASOURCE DAYOFSERVICE   TRIPID PROGRNUMBER STOPPOINTID  PLANNEDTIME_ARR  \
0         DB   2018-08-25  7329034          32         609            46010   
1         DB   2018-05-31  6847697          13         847            33619   
2         DB   2018-05-26  6780534          14        4758            57703   
3         DB   2018-04-23  6635422           7        7030            27325   
4         DB   2018-04-06  6606411          33        1453            85482   

   ACTUALTIME_ARR LINEID DIRECTION  
0           45900    29A         2  
1           33604    145         1  
2           57898     49         2  
3           27474    39A         2  
4           86219    123         2

In [13]:
dftrips = pd.read_csv('../../data/rt_trips_DB_2018.txt',sep=';')

dftrips.head()

DATASOURCE        DAYOFSERVICE   TRIPID LINEID  ROUTEID  DIRECTION  \
0         DB  07-FEB-18 00:00:00  6253783     68    68_80          1   
1         DB  07-FEB-18 00:00:00  6262138    25B  25B_271          2   
2         DB  07-FEB-18 00:00:00  6254942    45A   45A_70          2   
3         DB  07-FEB-18 00:00:00  6259460    25A  25A_273          1   
4         DB  07-FEB-18 00:00:00  6253175     14    14_15          1   

   PLANNEDTIME_ARR  PLANNEDTIME_DEP  ACTUALTIME_ARR  ACTUALTIME_DEP   BASIN  \
0            87245            84600         87524.0         84600.0  BasDef   
1            30517            26460         32752.0             NaN  BasDef   
2            35512            32100         36329.0         32082.0  BasDef   
3            57261            54420         58463.0         54443.0  BasDef   
4            85383            81600         84682.0         81608.0  BasDef   

   TENDERLOT  SUPPRESSED  JUSTIFICATIONID          LASTUPDATE       NOTE  
0        NaN         NaN              NaN  28-FEB-18 12:05:11  ,2967409,  
1        NaN         NaN              NaN  28-FEB-18 12:05:11  ,2580260,  
2        NaN         NaN              NaN  28-FEB-18 12:05:11  ,2448968,  
3        NaN         NaN              NaN  28-FEB-18 12:05:11  ,3094242,  
4        NaN         NaN              NaN  28-FEB-18 12:05:11  ,2526331,

In [14]:
dftrips.drop(['BASIN','TENDERLOT','SUPPRESSED','JUSTIFICATIONID','LASTUPDATE','NOTE','ROUTEID',],axis=1,inplace=True)

In [15]:
dftrips['DAYOFSERVICE'] = dftrips['DAYOFSERVICE'].astype('datetime64')

In [16]:
dftrips.head()

DATASOURCE DAYOFSERVICE   TRIPID LINEID  DIRECTION  PLANNEDTIME_ARR  \
0         DB   2018-02-07  6253783     68          1            87245   
1         DB   2018-02-07  6262138    25B          2            30517   
2         DB   2018-02-07  6254942    45A          2            35512   
3         DB   2018-02-07  6259460    25A          1            57261   
4         DB   2018-02-07  6253175     14          1            85383   

   PLANNEDTIME_DEP  ACTUALTIME_ARR  ACTUALTIME_DEP  
0            84600         87524.0         84600.0  
1            26460         32752.0             NaN  
2            32100         36329.0         32082.0  
3            54420         58463.0         54443.0  
4            81600         84682.0         81608.0

In [17]:
df_merged = df1_simple.merge(dftrips,how='left',on=['DATASOURCE','DAYOFSERVICE','TRIPID'])

In [18]:
df_merged.head()

DATASOURCE DAYOFSERVICE   TRIPID PROGRNUMBER STOPPOINTID  PLANNEDTIME_ARR_x  \
0         DB   2018-08-25  7329034          32         609              46010   
1         DB   2018-05-31  6847697          13         847              33619   
2         DB   2018-05-26  6780534          14        4758              57703   
3         DB   2018-04-23  6635422           7        7030              27325   
4         DB   2018-04-06  6606411          33        1453              85482   

   ACTUALTIME_ARR_x LINEID_x DIRECTION_x LINEID_y  DIRECTION_y  \
0             45900      29A           2      29A            2   
1             33604      145           1      145            1   
2             57898       49           2       49            2   
3             27474      39A           2      39A            2   
4             86219      123           2      123            2   

   PLANNEDTIME_ARR_y  PLANNEDTIME_DEP  ACTUALTIME_ARR_y  ACTUALTIME_DEP  
0              46917            44400           46687.0         44412.0  
1              36580            31800           36935.0         31849.0  
2              59829            56700           60642.0         56811.0  
3              31941            27000           33182.0         26927.0  
4              86085            83400           86860.0         83467.0

In [19]:
df_merged.drop(['LINEID_y','DIRECTION_y'],axis=1,inplace=True)
df_merged.rename(columns={'LINEID_x':'LINEID','DIRECTION_x':'DIRECTION'}, inplace=True)

In [20]:
df_merged['TRIP_FRAC'] = (df_merged['ACTUALTIME_ARR_y'] - df_merged['ACTUALTIME_ARR_x'])/(df_merged['ACTUALTIME_ARR_y'] - df_merged['PLANNEDTIME_DEP'])

In [91]:
stopfractions = df_merged.groupby(['LINEID','DIRECTION','STOPPOINTID'], as_index=False)['TRIP_FRAC'].mean().dropna()

In [93]:
stopfractions.reset_index(drop=True, inplace=True)

In [94]:
stopfractions.head()

LINEID DIRECTION STOPPOINTID  TRIP_FRAC
0      1         1          44   0.758086
1      1         1          45   0.728995
2      1         1          46   0.703364
3      1         1          47   0.681752
4      1         1          48   0.660377

In [95]:
stopfractionname = "stopfractions.pkl"
pickle.dump(stopfractions,open(stopfractionname,'wb'))

In [22]:
dftrips.head()

DATASOURCE DAYOFSERVICE   TRIPID LINEID  DIRECTION  PLANNEDTIME_ARR  \
0         DB   2018-02-07  6253783     68          1            87245   
1         DB   2018-02-07  6262138    25B          2            30517   
2         DB   2018-02-07  6254942    45A          2            35512   
3         DB   2018-02-07  6259460    25A          1            57261   
4         DB   2018-02-07  6253175     14          1            85383   

   PLANNEDTIME_DEP  ACTUALTIME_ARR  ACTUALTIME_DEP  
0            84600         87524.0         84600.0  
1            26460         32752.0             NaN  
2            32100         36329.0         32082.0  
3            54420         58463.0         54443.0  
4            81600         84682.0         81608.0

In [23]:
dftrips.drop(['TRIPID','DATASOURCE'],axis=1,inplace=True)

In [24]:
dftrips.head()

DAYOFSERVICE LINEID  DIRECTION  PLANNEDTIME_ARR  PLANNEDTIME_DEP  \
0   2018-02-07     68          1            87245            84600   
1   2018-02-07    25B          2            30517            26460   
2   2018-02-07    45A          2            35512            32100   
3   2018-02-07    25A          1            57261            54420   
4   2018-02-07     14          1            85383            81600   

   ACTUALTIME_ARR  ACTUALTIME_DEP  
0         87524.0         84600.0  
1         32752.0             NaN  
2         36329.0         32082.0  
3         58463.0         54443.0  
4         84682.0         81608.0

In [25]:
dftrips.dropna(inplace=True)

In [26]:
dftrips.dtypes

DAYOFSERVICE       datetime64[ns]
LINEID                     object
DIRECTION                   int64
PLANNEDTIME_ARR             int64
PLANNEDTIME_DEP             int64
ACTUALTIME_ARR            float64
ACTUALTIME_DEP            float64
dtype: object

In [27]:
dftrips['DIRECTION'] = dftrips['DIRECTION'].astype('category')
dftrips['LINEID'] = dftrips['LINEID'].astype('category')
dftrips['ACTUALTIME_ARR'] = dftrips['ACTUALTIME_ARR'].astype('int64')
dftrips['ACTUALTIME_DEP'] = dftrips['ACTUALTIME_DEP'].astype('int64')
dftrips['LINEID'] = dftrips['LINEID'].astype('category')

In [28]:
dftrips['TRIPLENGTH'] = dftrips['ACTUALTIME_ARR'] - dftrips['ACTUALTIME_DEP']
dftrips['dt'] = dftrips['DAYOFSERVICE'] + pd.to_timedelta(dftrips['ACTUALTIME_DEP'], unit='s')

In [29]:
dftrips.head()

DAYOFSERVICE LINEID DIRECTION  PLANNEDTIME_ARR  PLANNEDTIME_DEP  \
0   2018-02-07     68         1            87245            84600   
2   2018-02-07    45A         2            35512            32100   
3   2018-02-07    25A         1            57261            54420   
4   2018-02-07     14         1            85383            81600   
5   2018-02-07    77A         2            41648            37200   

   ACTUALTIME_ARR  ACTUALTIME_DEP  TRIPLENGTH                  dt  
0           87524           84600        2924 2018-02-07 23:30:00  
2           36329           32082        4247 2018-02-07 08:54:42  
3           58463           54443        4020 2018-02-07 15:07:23  
4           84682           81608        3074 2018-02-07 22:40:08  
5           42019           37538        4481 2018-02-07 10:25:38

In [30]:
categorical_columns = dftrips.select_dtypes('category').columns
numerical_columns = dftrips.select_dtypes('int64').columns

In [31]:
dftrips.head()

DAYOFSERVICE LINEID DIRECTION  PLANNEDTIME_ARR  PLANNEDTIME_DEP  \
0   2018-02-07     68         1            87245            84600   
2   2018-02-07    45A         2            35512            32100   
3   2018-02-07    25A         1            57261            54420   
4   2018-02-07     14         1            85383            81600   
5   2018-02-07    77A         2            41648            37200   

   ACTUALTIME_ARR  ACTUALTIME_DEP  TRIPLENGTH                  dt  
0           87524           84600        2924 2018-02-07 23:30:00  
2           36329           32082        4247 2018-02-07 08:54:42  
3           58463           54443        4020 2018-02-07 15:07:23  
4           84682           81608        3074 2018-02-07 22:40:08  
5           42019           37538        4481 2018-02-07 10:25:38

In [32]:
dftrips[categorical_columns].describe().T

count unique  top    freq
LINEID     1893367    130  46A   68840
DIRECTION  1893367      2    1  948722

In [33]:
dftrips[numerical_columns].describe().T

count          mean           std      min      25%  \
PLANNEDTIME_ARR  1893367.0  54818.775044  17283.826881  18203.0  39622.0   
PLANNEDTIME_DEP  1893367.0  51298.936625  17434.197250  16200.0  36000.0   
ACTUALTIME_ARR   1893367.0  55188.713192  17279.896452  17546.0  39938.0   
ACTUALTIME_DEP   1893367.0  51334.954109  17439.580453  16187.0  36055.0   
TRIPLENGTH       1893367.0   3853.759083   1434.782157 -14866.0   2803.0   

                     50%      75%      max  
PLANNEDTIME_ARR  54816.0  68651.0  91680.0  
PLANNEDTIME_DEP  51120.0  64800.0  87600.0  
ACTUALTIME_ARR   55224.0  69073.0  94378.0  
ACTUALTIME_DEP   51179.0  64841.0  97177.0  
TRIPLENGTH        3772.0   4845.0  23458.0

In [34]:
dftrips[dftrips['TRIPLENGTH'] < 0].sort_values('ACTUALTIME_ARR',ascending=True)

DAYOFSERVICE LINEID DIRECTION  PLANNEDTIME_ARR  PLANNEDTIME_DEP  \
726144    2018-02-15     41         1            20548            18000   
1917111   2018-10-23     42         2            24331            21600   
1482678   2018-08-25     14         2            24414            23400   
520908    2018-11-08    123         2            26638            23400   
2049497   2018-10-27     11         1            27703            25200   
...              ...    ...       ...              ...              ...   
1051262   2018-10-05    77A         1            82797            79200   
1975479   2018-01-24    150         1            84572            82800   
411291    2018-07-28    111         2            84912            84600   
212027    2018-02-07     13         1            85251            83700   
339290    2018-07-06    120         2            85653            84600   

         ACTUALTIME_ARR  ACTUALTIME_DEP  TRIPLENGTH                  dt  
726144            20186           21595       -1409 2018-02-15 05:59:55  
1917111           24630           25205        -575 2018-10-23 07:00:05  
1482678           24693           26968       -2275 2018-08-25 07:29:28  
520908            27078           28494       -1416 2018-11-08 07:54:54  
2049497           28773           28811         -38 2018-10-27 08:00:11  
...                 ...             ...         ...                 ...  
1051262           84265           97064      -12799 2018-10-06 02:57:44  
1975479           84317           85282        -965 2018-01-24 23:41:22  
411291            84928           86089       -1161 2018-07-28 23:54:49  
212027            85852           88912       -3060 2018-02-08 00:41:52  
339290            85923           86047        -124 2018-07-06 23:54:07  

[103 rows x 9 columns]

In [35]:
dftrips = dftrips[dftrips['TRIPLENGTH'] > 0]

In [36]:
dftrips.drop(['ACTUALTIME_ARR','ACTUALTIME_DEP'],axis=1,inplace=True)

In [37]:
dftrips.head()

DAYOFSERVICE LINEID DIRECTION  PLANNEDTIME_ARR  PLANNEDTIME_DEP  TRIPLENGTH  \
0   2018-02-07     68         1            87245            84600        2924   
2   2018-02-07    45A         2            35512            32100        4247   
3   2018-02-07    25A         1            57261            54420        4020   
4   2018-02-07     14         1            85383            81600        3074   
5   2018-02-07    77A         2            41648            37200        4481   

                   dt  
0 2018-02-07 23:30:00  
2 2018-02-07 08:54:42  
3 2018-02-07 15:07:23  
4 2018-02-07 22:40:08  
5 2018-02-07 10:25:38

In [38]:
dftrips['MONTH'] = dftrips['DAYOFSERVICE'].dt.month.astype('category')
dftrips['WEEKDAY'] = dftrips['DAYOFSERVICE'].dt.weekday.astype('category')
dftrips['WEEKEND'] = dftrips['WEEKDAY'].map(lambda x: x in [5,6]).astype('category')
dftrips['RUSH_HOUR'] = dftrips['PLANNEDTIME_DEP'].map(lambda x : (25200 < x  < 32400) or (57600 < x < 68400)).astype('category')
dftrips.drop(['DAYOFSERVICE'],axis=1,inplace=True)

In [39]:
dftrips[dftrips['WEEKEND'] == True]

LINEID DIRECTION  PLANNEDTIME_ARR  PLANNEDTIME_DEP  TRIPLENGTH  \
38         185         1            58751            57000        1873   
39         185         1            63551            61800        2216   
40         185         1            68351            66600        1937   
41          16         1            37539            33600        4174   
42          16         1            35139            31200        3954   
...        ...       ...              ...              ...         ...   
2178050     11         2            49690            46200        4036   
2178051     11         2            55090            51600        3605   
2178052     11         2            53290            49800        3534   
2178053     11         2            47890            44400        4177   
2178055     76         2            78392            76500        2032   

                         dt MONTH WEEKDAY WEEKEND RUSH_HOUR  
38      2018-02-18 15:49:21     2       6    True     False  
39      2018-02-18 17:13:33     2       6    True      True  
40      2018-02-18 18:29:59     2       6    True      True  
41      2018-02-18 09:21:50     2       6    True     False  
42      2018-02-18 08:40:24     2       6    True      True  
...                     ...   ...     ...     ...       ...  
2178050 2018-05-27 12:50:14     5       6    True     False  
2178051 2018-05-27 14:19:33     5       6    True     False  
2178052 2018-05-27 13:49:54     5       6    True     False  
2178053 2018-05-27 12:22:08     5       6    True     False  
2178055 2018-05-27 21:14:26     5       6    True     False  

[394411 rows x 10 columns]

In [40]:
dftrips.head()

LINEID DIRECTION  PLANNEDTIME_ARR  PLANNEDTIME_DEP  TRIPLENGTH  \
0     68         1            87245            84600        2924   
2    45A         2            35512            32100        4247   
3    25A         1            57261            54420        4020   
4     14         1            85383            81600        3074   
5    77A         2            41648            37200        4481   

                   dt MONTH WEEKDAY WEEKEND RUSH_HOUR  
0 2018-02-07 23:30:00     2       2   False     False  
2 2018-02-07 08:54:42     2       2   False      True  
3 2018-02-07 15:07:23     2       2   False     False  
4 2018-02-07 22:40:08     2       2   False     False  
5 2018-02-07 10:25:38     2       2   False     False

In [41]:
dftrips['PLANNEDTIME_DEP_COS'] = np.cos(2*np.pi*dftrips['PLANNEDTIME_DEP']/(60*60*24))
dftrips['PLANNEDTIME_DEP_SIN'] = np.sin(2*np.pi*dftrips['PLANNEDTIME_DEP']/(60*60*24))

### Add Weather

In [114]:
df_weather = pd.read_csv('../../data/historic_weather_data.csv')

In [115]:
df_weather.head()

dt                         dt_iso  timezone city_name        lat  \
0  1483228800  2017-01-01 00:00:00 +0000 UTC         0    Dublin  53.349805   
1  1483232400  2017-01-01 01:00:00 +0000 UTC         0    Dublin  53.349805   
2  1483236000  2017-01-01 02:00:00 +0000 UTC         0    Dublin  53.349805   
3  1483239600  2017-01-01 03:00:00 +0000 UTC         0    Dublin  53.349805   
4  1483243200  2017-01-01 04:00:00 +0000 UTC         0    Dublin  53.349805   

       lon  temp  feels_like  temp_min  temp_max  ...  wind_deg  rain_1h  \
0 -6.26031  5.89        1.16      5.00      9.17  ...       330      NaN   
1 -6.26031  5.06        0.88      4.80      6.24  ...       310      NaN   
2 -6.26031  5.04        0.85      4.23      6.21  ...       320      NaN   
3 -6.26031  4.59       -1.15      4.00      6.14  ...       330      NaN   
4 -6.26031  4.15       -1.86      3.96      5.89  ...       330      NaN   

   rain_3h  snow_1h  snow_3h  clouds_all  weather_id  weather_main  \
0      NaN      NaN      NaN          75         500          Rain   
1      NaN      NaN      NaN          75         500          Rain   
2      NaN      NaN      NaN          75         803        Clouds   
3      NaN      NaN      NaN          75         803        Clouds   
4      NaN      NaN      NaN          75         803        Clouds   

   weather_description  weather_icon  
0           light rain           10n  
1           light rain           10n  
2        broken clouds           04n  
3        broken clouds           04n  
4        broken clouds           04n  

[5 rows x 25 columns]

In [118]:
df_weather.dtypes

dt                       int64
dt_iso                  object
timezone                 int64
city_name               object
lat                    float64
lon                    float64
temp                   float64
feels_like             float64
temp_min               float64
temp_max               float64
pressure                 int64
sea_level              float64
grnd_level             float64
humidity                 int64
wind_speed             float64
wind_deg                 int64
rain_1h                float64
rain_3h                float64
snow_1h                float64
snow_3h                float64
clouds_all               int64
weather_id               int64
weather_main            object
weather_description     object
weather_icon            object
dtype: object

In [119]:
df_weather.drop([
    'city_name',
    'timezone',
    'weather_icon',
    'weather_description',
    'sea_level',
    'grnd_level',
    'lon',
    'lat',
    'dt_iso',
    'weather_id',
    'rain_1h',
    'rain_3h',
    'snow_1h',
    'snow_3h',
    'clouds_all',
    'temp_min',
    'temp_max',
    'pressure',
    'humidity',
    'wind_speed',
    'wind_deg',
    'temp'
],axis=1,inplace=True)

In [120]:
df_weather.dtypes

dt                int64
feels_like      float64
weather_main     object
dtype: object

In [121]:
df_weather['weather_main'] = df_weather['weather_main'].astype('category')

In [122]:
import datetime

df_weather['dt'] = pd.to_datetime(df_weather['dt'], unit='s')

In [123]:
df_weather.head()

dt  feels_like weather_main
0 2017-01-01 00:00:00        1.16         Rain
1 2017-01-01 01:00:00        0.88         Rain
2 2017-01-01 02:00:00        0.85       Clouds
3 2017-01-01 03:00:00       -1.15       Clouds
4 2017-01-01 04:00:00       -1.86       Clouds

In [124]:
df_weather['month'] = df_weather['dt'].dt.month

In [154]:
avg_monthly_temp = df_weather.groupby('month')['feels_like'].mean()
avg_monthly_weather = df_weather.groupby('month')['weather_main'].agg(lambda x:x.value_counts().index[0])

avg_monthly_weather = pd.DataFrame({'feels_like':avg_monthly_temp,'weather_main':avg_monthly_weather})
avg_monthly_weather.tail()

feels_like weather_main
month                         
8       12.500821       Clouds
9        9.372250       Clouds
10       6.160408       Clouds
11       2.620289       Clouds
12       1.757549       Clouds

In [155]:
wloc = 'avg_monthly_weather.pkl'
pickle.dump(avg_monthly_weather,open(wloc,'wb'))

In [49]:
dftrips = pd.merge_asof(dftrips.sort_values('dt'),df_weather)

In [50]:
dftrips.drop('dt',axis=1,inplace=True)

In [51]:
dftrips.dtypes

LINEID                 category
DIRECTION              category
PLANNEDTIME_ARR           int64
PLANNEDTIME_DEP           int64
TRIPLENGTH                int64
MONTH                  category
WEEKDAY                category
WEEKEND                category
RUSH_HOUR              category
PLANNEDTIME_DEP_COS     float64
PLANNEDTIME_DEP_SIN     float64
feels_like              float64
weather_main           category
dtype: object

In [52]:
print(dftrips.shape)
dfs = dict()
for line in dftrips['LINEID'].unique():
    dfs[line] = dict()
    for direction in dftrips[dftrips['LINEID'] == line]['DIRECTION'].unique():
        dfs[line][direction] = dftrips[dftrips['LINEID'] == line][dftrips['DIRECTION'] == direction].drop(['LINEID','DIRECTION'],axis=1)

(1893264, 13)


C:\Users\Mesel\Anaconda3\lib\site-packages\ipykernel_launcher.py:6: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  


In [53]:
dftrips.head()

LINEID DIRECTION  PLANNEDTIME_ARR  PLANNEDTIME_DEP  TRIPLENGTH MONTH  \
0     66         1            28733            25500        3777     1   
1    77A         1            28947            25800        3260     1   
2     41         2            27785            26100        1473     1   
3     83         1            29314            26400        2758     1   
4    130         2            28305            27000        1044     1   

  WEEKDAY WEEKEND RUSH_HOUR  PLANNEDTIME_DEP_COS  PLANNEDTIME_DEP_SIN  \
0       0   False      True            -0.279829             0.960050   
1       0   False      True            -0.300706             0.953717   
2       0   False      True            -0.321439             0.946930   
3       0   False      True            -0.342020             0.939693   
4       0   False      True            -0.382683             0.923880   

   feels_like weather_main  
0        -1.5       Clouds  
1        -1.5       Clouds  
2        -1.5       Clouds  
3        -1.5       Clouds  
4        -1.5       Clouds

In [54]:
# dftrips.drop(['PLANNEDTIME_DEP_COS','PLANNEDTIME_DEP_SIN'],axis=1,inplace=True)
# dftrips.drop('MONTH',axis=1,inplace=True)
# dftrips.drop('WEEKDAY',axis=1,inplace=True)

In [55]:
dftrips.dtypes

LINEID                 category
DIRECTION              category
PLANNEDTIME_ARR           int64
PLANNEDTIME_DEP           int64
TRIPLENGTH                int64
MONTH                  category
WEEKDAY                category
WEEKEND                category
RUSH_HOUR              category
PLANNEDTIME_DEP_COS     float64
PLANNEDTIME_DEP_SIN     float64
feels_like              float64
weather_main           category
dtype: object

In [56]:
def gen_models(model,dfs,max_iter=200):
    models = dict()
    train_test = dict()
    for route in dfs:
        models[route] = dict()
        train_test[route] = dict()
        for direction in dfs[route]:
            train_test[route][direction] = dict()
            df_rev1 = pd.get_dummies(dfs[route][direction])
        
#             print(route, direction)
            # y is the target
            y = df_rev1["TRIPLENGTH"]
            # X is everything else
            X = df_rev1.drop(["TRIPLENGTH"],1)
            # Split the dataset into two datasets: 70% training and 30% test
            X_train, X_test, y_train, y_test = train_test_split(X, y, random_state=1,  test_size=0.3)

#             timetabled_values_train = X_train['PLANNEDTIME_ARR'] - X_train['PLANNEDTIME_DEP']
    #         timetabled_values_test = X_test['PLANNEDTIME_ARR'] - X_test['PLANNEDTIME_DEP']
            
    #         X_train.drop('PLANNEDTIME_ARR',axis=1,inplace=True)
    #         X_test.drop('PLANNEDTIME_ARR',axis=1,inplace=True)
    #         X_train.drop('PLANNEDTIME_DEP',axis=1,inplace=True)
    #         X_test.drop('PLANNEDTIME_DEP',axis=1,inplace=True)
            
    #         print("original range is: ",df_rev1.shape[0])
    #         print("training range (70%):\t rows 0 to", round(X_train.shape[0]))
    #         print("test range (30%): \t rows", round(X_train.shape[0]), "to", round(X_train.shape[0]) + X_test.shape[0])
            
            # need to reset the index to allow contatenation with predicted values otherwise not joining on same index...
            X_train.reset_index(drop=True, inplace=True)
            y_train.reset_index(drop=True, inplace=True)
            X_test.reset_index(drop=True, inplace=True)
            y_test.reset_index(drop=True, inplace=True)
            X_train.head(5)
        
            timetabled_values_train = X_train['PLANNEDTIME_ARR'] - X_train['PLANNEDTIME_DEP']
            timetabled_values_test = X_test['PLANNEDTIME_ARR'] - X_test['PLANNEDTIME_DEP']
            X_train.drop('PLANNEDTIME_ARR',axis=1,inplace=True)
            X_test.drop('PLANNEDTIME_ARR',axis=1,inplace=True)
            X_train.drop('PLANNEDTIME_DEP',axis=1,inplace=True)
            X_test.drop('PLANNEDTIME_DEP',axis=1,inplace=True)
            
            if model == MLPRegressor:
                output_model = model(max_iter=max_iter).fit(X_train, y_train)
            else: 
                output_model = model().fit(X_train, y_train)
            
            models[route][direction] = output_model
            train_test[route][direction] = {
                'X_train':X_train,
                'X_test':X_test,
                'y_train':y_train,
                'y_test':y_test,
                'timetabled_values_train':timetabled_values_train,
                'timetabled_values_test':timetabled_values_test
            }
    return models, train_test

In [57]:
models_LR, train_test_LR = gen_models(LinearRegression,dfs)

C:\Users\Mesel\Anaconda3\lib\site-packages\pandas\core\frame.py:3997: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  errors=errors,
C:\Users\Mesel\Anaconda3\lib\site-packages\pandas\core\frame.py:3997: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  errors=errors,
C:\Users\Mesel\Anaconda3\lib\site-packages\pandas\core\frame.py:3997: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  errors=errors,
C:\Users\Mesel\Anaconda3\lib\site-packages\pan

C:\Users\Mesel\Anaconda3\lib\site-packages\pandas\core\frame.py:3997: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  errors=errors,
C:\Users\Mesel\Anaconda3\lib\site-packages\pandas\core\frame.py:3997: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  errors=errors,
C:\Users\Mesel\Anaconda3\lib\site-packages\pandas\core\frame.py:3997: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  errors=errors,
C:\Users\Mesel\Anaconda3\lib\site-packages\pan

C:\Users\Mesel\Anaconda3\lib\site-packages\pandas\core\frame.py:3997: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  errors=errors,
C:\Users\Mesel\Anaconda3\lib\site-packages\pandas\core\frame.py:3997: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  errors=errors,
C:\Users\Mesel\Anaconda3\lib\site-packages\pandas\core\frame.py:3997: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  errors=errors,
C:\Users\Mesel\Anaconda3\lib\site-packages\pan

C:\Users\Mesel\Anaconda3\lib\site-packages\pandas\core\frame.py:3997: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  errors=errors,
C:\Users\Mesel\Anaconda3\lib\site-packages\pandas\core\frame.py:3997: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  errors=errors,
C:\Users\Mesel\Anaconda3\lib\site-packages\pandas\core\frame.py:3997: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  errors=errors,
C:\Users\Mesel\Anaconda3\lib\site-packages\pan

C:\Users\Mesel\Anaconda3\lib\site-packages\pandas\core\frame.py:3997: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  errors=errors,
C:\Users\Mesel\Anaconda3\lib\site-packages\pandas\core\frame.py:3997: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  errors=errors,
C:\Users\Mesel\Anaconda3\lib\site-packages\pandas\core\frame.py:3997: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  errors=errors,
C:\Users\Mesel\Anaconda3\lib\site-packages\pan

C:\Users\Mesel\Anaconda3\lib\site-packages\pandas\core\frame.py:3997: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  errors=errors,
C:\Users\Mesel\Anaconda3\lib\site-packages\pandas\core\frame.py:3997: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  errors=errors,
C:\Users\Mesel\Anaconda3\lib\site-packages\pandas\core\frame.py:3997: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  errors=errors,
C:\Users\Mesel\Anaconda3\lib\site-packages\pan

C:\Users\Mesel\Anaconda3\lib\site-packages\pandas\core\frame.py:3997: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  errors=errors,
C:\Users\Mesel\Anaconda3\lib\site-packages\pandas\core\frame.py:3997: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  errors=errors,
C:\Users\Mesel\Anaconda3\lib\site-packages\pandas\core\frame.py:3997: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  errors=errors,
C:\Users\Mesel\Anaconda3\lib\site-packages\pan

C:\Users\Mesel\Anaconda3\lib\site-packages\pandas\core\frame.py:3997: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  errors=errors,
C:\Users\Mesel\Anaconda3\lib\site-packages\pandas\core\frame.py:3997: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  errors=errors,
C:\Users\Mesel\Anaconda3\lib\site-packages\pandas\core\frame.py:3997: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  errors=errors,
C:\Users\Mesel\Anaconda3\lib\site-packages\pan

C:\Users\Mesel\Anaconda3\lib\site-packages\pandas\core\frame.py:3997: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  errors=errors,
C:\Users\Mesel\Anaconda3\lib\site-packages\pandas\core\frame.py:3997: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  errors=errors,
C:\Users\Mesel\Anaconda3\lib\site-packages\pandas\core\frame.py:3997: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  errors=errors,
C:\Users\Mesel\Anaconda3\lib\site-packages\pan

In [58]:
def mean_absolute_percentage_error(y_true, y_pred): 
#     y_true, y_pred = check_arrays(y_true, y_pred)

    ## Note: does not handle mix 1d representation
    #if _is_1d(y_true): 
    #    y_true, y_pred = _check_1d_array(y_true, y_pred)

    return np.mean(np.abs((y_true - y_pred) / y_true)) * 100


#This function is used repeatedly to compute all metrics
def printMetrics(testActualVal, predictions,timetabled_values):
    #classification evaluation measures
    print('\n==============================================================================')
    print("MAE: ", metrics.mean_absolute_error(testActualVal, predictions))
    #print("MSE: ", metrics.mean_squared_error(testActualVal, predictions))
    print("RMSE: ", metrics.mean_squared_error(testActualVal, predictions)**0.5)
    print("R2: ", metrics.r2_score(testActualVal, predictions))
    print("MAPE: ", mean_absolute_percentage_error(testActualVal, predictions))
    print()
    
    print("MAE: ", metrics.mean_absolute_error(testActualVal, timetabled_values))
    #print("MSE: ", metrics.mean_squared_error(testActualVal, predictions))
    print("RMSE: ", metrics.mean_squared_error(testActualVal, timetabled_values)**0.5)
    print("R2: ", metrics.r2_score(testActualVal, timetabled_values))
    print("MAPE: ", mean_absolute_percentage_error(testActualVal, timetabled_values))


In [59]:
def multiMetrics(models,train_test,train_or_test,printall=False):
    RMSE = 0
    timetable_RMSE = 0
    MAPE = 0
    timetable_MAPE = 0
    count = 0
    badroutes = dict()
    for route in models:
        for direction in models[route]:
            X_train = train_test[route][direction]['X_'+train_or_test]
            y_train = train_test[route][direction]['y_'+train_or_test]
            timetabled_values_train = train_test[route][direction]['timetabled_values_'+train_or_test]
            try:
                predictions_train = models[route][direction].predict(X_train)
        
        #         print(predictions_train/y_train)
        
    
                RMSE += metrics.mean_squared_error(y_train, predictions_train)**0.5
                timetable_RMSE += metrics.mean_squared_error(y_train, timetabled_values_train)**0.5

                MAPE += mean_absolute_percentage_error(y_train, predictions_train)
                timetable_MAPE += mean_absolute_percentage_error(y_train, timetabled_values_train)
        
                count += 1
                if printall == True:
                    print(route, direction)
                    printMetrics(y_train,predictions_train,timetabled_values_train)
                    print("Training set size: ", X_train.size)
                    
                if metrics.mean_squared_error(y_train, predictions_train)**0.5 > metrics.mean_squared_error(y_train, timetabled_values_train)**0.5:
                    badroutes[route + "_" + str(direction)] = {
                        'training_size':X_train.size,
                        'abs_percent_difference': mean_absolute_percentage_error(y_train, predictions_train) - mean_absolute_percentage_error(y_train, timetabled_values_train)
                    }
            except:
                pass
            
    print()
    print('Average model RMSE: ', RMSE/count)
    print('Average timetable RMSE: ', timetable_RMSE/count)
    print()
    print('Average model MAPE: ', MAPE/count)
    print('Average timetable MAPE: ', timetable_MAPE/count)
    print()
    print('Bad routes:' )
    print('---')
    for route in badroutes:
        print(route, '\t', badroutes[route]['training_size'], '\t', badroutes[route]['abs_percent_difference'])
    print()
    print("Total bad routes: %s"%len(badroutes.keys()))

multiMetrics(models_LR,train_test_LR,'train')

multiMetrics(models_LR,train_test_LR,'test')

mkdir -p LR1

mname = 'LR1/models.pkl'
ttname = 'LR1/train_test.pkl'
pickle.dump(models_LR,open(mname,'wb'))
pickle.dump(train_test_LR,open(ttname,'wb'))

models_KNR, train_test_KNR = gen_models(KNeighborsRegressor,dfs)

multiMetrics(models_KNR,train_test_KNR,'train')

multiMetrics(models_KNR,train_test_KNR,'test',printall=True)

mkdir KNR1

mname = 'KNR1/models.pkl'
ttname = 'KNR1/train_test.pkl'
pickle.dump(models_KNR,open(mname,'wb'))
pickle.dump(train_test_KNR,open(ttname,'wb'))

import warnings
warnings.filterwarnings('ignore')

import time
time1 = time.time()

models_NN_200, train_test_NN_200 = gen_models(MLPRegressor,dfs,max_iter=200)
print()
print("Seconds taken: ", time.time()-time1)

multiMetrics(models_NN_200,train_test_NN_200,'train',printall=False)

multiMetrics(models_NN_200,train_test_NN_200,'test',printall=False)

mkdir NN_200

mname = 'NN_200/models.pkl'
ttname = 'NN_200/train_test.pkl'
pickle.dump(models_NN_200,open(mname,'wb'))
pickle.dump(train_test_NN_200,open(ttname,'wb'))

import warnings
warnings.filterwarnings('ignore')

import time
time1 = time.time()

models_NN_500, train_test_NN_500 = gen_models(MLPRegressor,dfs,max_iter=500)
print()
print("Seconds taken: ", time.time()-time1)

multiMetrics(models_NN_500,train_test_NN_500,'train',printall=False)

multiMetrics(models_NN_500,train_test_NN_500,'test',printall=False)

mname = 'NN_500/models.pkl'
ttname = 'NN_500/train_test.pkl'
pickle.dump(models_NN_500,open(mname,'wb'))
pickle.dump(train_test_NN_500,open(ttname,'wb'))

warnings.filterwarnings('ignore')

time1 = time.time()

models_NN_1000, train_test_NN_1000 = gen_models(MLPRegressor,dfs,max_iter=1000)
print()
print("Seconds taken: ", time.time()-time1)

multiMetrics(models_NN_1000,train_test_NN_1000,'train',printall=False)

multiMetrics(models_NN_1000,train_test_NN_1000,'test',printall=False)

mname = 'NN_1000/models.pkl'
ttname = 'NN_1000/train_test.pkl'
pickle.dump(models_NN_1000,open(mname,'wb'))
pickle.dump(train_test_NN_1000,open(ttname,'wb'))

warnings.filterwarnings('ignore')

time1 = time.time()

models_NN_2000, train_test_NN_2000 = gen_models(MLPRegressor,dfs,max_iter=2000)
print()
print("Seconds taken: ", time.time()-time1)

multiMetrics(models_NN_2000,train_test_NN_2000,'train',printall=False)

multiMetrics(models_NN_2000,train_test_NN_2000,'test',printall=False)

mname = 'NN_2000/models.pkl'
ttname = 'NN_2000/train_test.pkl'
pickle.dump(models_NN_2000,open(mname,'wb'))
pickle.dump(train_test_NN_2000,open(ttname,'wb'))

from multiprocessing import Process, Manager

In [60]:
def pool_process(f, data, pool_size):
    import multiprocessing
    from multiprocessing import Pool
    
    print('No. Inputs: %s, pool_size: %s'%(len(data),pool_size))
    tp1 = time.time()
    pool = Pool(processes=pool_size) # initialize the Pool.
    result = pool.map(f, data)       # map f to the data using the Pool of processes to do the work 
    pool.close() # No more processes
    pool.join()  # Wait for the pool processing to complete. 
    return result

warnings.filterwarnings('ignore')

time1 = time.time()

models_NN_test = pool_process(MLPRegressor,dfs,2)
print()
print("Seconds taken: ", time.time()-time1)

type(models_NN_test)

In [61]:
def gen_NN_mult(key):
    df_rev1 = pd.get_dummies(dfs2[key])
        
#   print(route, direction)
    # y is the target
    y = df_rev1["TRIPLENGTH"]
    # X is everything else
    X = df_rev1.drop(["TRIPLENGTH"],1)
    # Split the dataset into two datasets: 70% training and 30% test
    X_train, X_test, y_train, y_test = train_test_split(X, y, random_state=1,  test_size=0.3)

#   timetabled_values_train = X_train['PLANNEDTIME_ARR'] - X_train['PLANNEDTIME_DEP']
#   timetabled_values_test = X_test['PLANNEDTIME_ARR'] - X_test['PLANNEDTIME_DEP']
            
#   X_train.drop('PLANNEDTIME_ARR',axis=1,inplace=True)
#   X_test.drop('PLANNEDTIME_ARR',axis=1,inplace=True)
#   X_train.drop('PLANNEDTIME_DEP',axis=1,inplace=True)
#   X_test.drop('PLANNEDTIME_DEP',axis=1,inplace=True)
            
#   print("original range is: ",df_rev1.shape[0])
#   print("training range (70%):\t rows 0 to", round(X_train.shape[0]))
#   print("test range (30%): \t rows", round(X_train.shape[0]), "to", round(X_train.shape[0]) + X_test.shape[0])
            
# need to reset the index to allow contatenation with predicted values otherwise not joining on same index...
    X_train.reset_index(drop=True, inplace=True)
    y_train.reset_index(drop=True, inplace=True)
    X_test.reset_index(drop=True, inplace=True)
    y_test.reset_index(drop=True, inplace=True)
    X_train.head(5)
        
    timetabled_values_train = X_train['PLANNEDTIME_ARR'] - X_train['PLANNEDTIME_DEP']
    timetabled_values_test = X_test['PLANNEDTIME_ARR'] - X_test['PLANNEDTIME_DEP']
    X_train.drop('PLANNEDTIME_ARR',axis=1,inplace=True)
    X_test.drop('PLANNEDTIME_ARR',axis=1,inplace=True)
    X_train.drop('PLANNEDTIME_DEP',axis=1,inplace=True)
    X_test.drop('PLANNEDTIME_DEP',axis=1,inplace=True)
    
    output_model = MLPRegressor(max_iter=2).fit(X_train, y_train)
    test_train_dict[key] = {
                'X_train':X_train,
                'X_test':X_test,
                'y_train':y_train,
                'y_test':y_test,
                'timetabled_values_train':timetabled_values_train,
                'timetabled_values_test':timetabled_values_test
            }
    
    return output_model

In [62]:
dfs2 = dict()
for line in dftrips['LINEID'].unique():
    for direction in dftrips[dftrips['LINEID'] == line]['DIRECTION'].unique():
        dfs2[line+'_'+str(direction)] = dftrips[dftrips['LINEID'] == line][dftrips['DIRECTION'] == direction]

C:\Users\Mesel\Anaconda3\lib\site-packages\ipykernel_launcher.py:4: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  after removing the cwd from sys.path.


In [63]:
print(dfs2)

{'66_1':         LINEID DIRECTION  PLANNEDTIME_ARR  PLANNEDTIME_DEP  TRIPLENGTH MONTH  \
0           66         1            28733            25500        3777     1   
119         66         1            36533            33300        3160     1   
214         66         1            38933            35700        3388     1   
412         66         1            43044            39300        3200     1   
632         66         1            46644            42900        3240     1   
...        ...       ...              ...              ...         ...   ...   
1892862     66         1            74442            71100        4313    12   
1892965     66         1            76242            72900        3718    12   
1893072     66         1            78042            74700        3929    12   
1893157     66         1            79778            76500        3181    12   
1893229     66         1            81578            78300        3706    12   

        WEEKDAY WEEKEND RUSH_H

In [64]:
import mult_funcs 

test_train_dict = {}
        
# import warnings
# warnings.filterwarnings('ignore')

import time
time1 = time.time()

dfs2 = [item for item in dfs2.values()]
models_NN_test = pool_process(mult_funcs.gen_NN_mult,dfs2,4)
print()
print("Seconds taken: ", time.time()-time1)

No. Inputs: 252, pool_size: 4

Seconds taken:  100.39879703521729


In [65]:
def gen_NN_mult(df):
    df_rev1 = pd.get_dummies(df)
        
#   print(route, direction)
    # y is the target
    y = df_rev1["TRIPLENGTH"]
    # X is everything else
    X = df_rev1.drop(["TRIPLENGTH"],1)
    # Split the dataset into two datasets: 70% training and 30% test
    X_train, X_test, y_train, y_test = train_test_split(X, y, random_state=1,  test_size=0.3)

#   timetabled_values_train = X_train['PLANNEDTIME_ARR'] - X_train['PLANNEDTIME_DEP']
#   timetabled_values_test = X_test['PLANNEDTIME_ARR'] - X_test['PLANNEDTIME_DEP']
            
#   X_train.drop('PLANNEDTIME_ARR',axis=1,inplace=True)
#   X_test.drop('PLANNEDTIME_ARR',axis=1,inplace=True)
#   X_train.drop('PLANNEDTIME_DEP',axis=1,inplace=True)
#   X_test.drop('PLANNEDTIME_DEP',axis=1,inplace=True)
            
#   print("original range is: ",df_rev1.shape[0])
#   print("training range (70%):\t rows 0 to", round(X_train.shape[0]))
#   print("test range (30%): \t rows", round(X_train.shape[0]), "to", round(X_train.shape[0]) + X_test.shape[0])
            
# need to reset the index to allow contatenation with predicted values otherwise not joining on same index...
    X_train.reset_index(drop=True, inplace=True)
    y_train.reset_index(drop=True, inplace=True)
    X_test.reset_index(drop=True, inplace=True)
    y_test.reset_index(drop=True, inplace=True)
    X_train.head(5)
        
    timetabled_values_train = X_train['PLANNEDTIME_ARR'] - X_train['PLANNEDTIME_DEP']
    timetabled_values_test = X_test['PLANNEDTIME_ARR'] - X_test['PLANNEDTIME_DEP']
    X_train.drop('PLANNEDTIME_ARR',axis=1,inplace=True)
    X_test.drop('PLANNEDTIME_ARR',axis=1,inplace=True)
    X_train.drop('PLANNEDTIME_DEP',axis=1,inplace=True)
    X_test.drop('PLANNEDTIME_DEP',axis=1,inplace=True)
    
    output_model = MLPRegressor(max_iter=2).fit(X_train, y_train)
#     test_train_dict[key] = {
#                 'X_train':X_train,
#                 'X_test':X_test,
#                 'y_train':y_train,
#                 'y_test':y_test,
#                 'timetabled_values_train':timetabled_values_train,
#                 'timetabled_values_test':timetabled_values_test
#             }
    
    return output_model

In [66]:
len(models_NN_test)

252

In [67]:
def unnormalise(x_norm,x_max,x_min):
    return (x_max - x_min)*x_norm + x_min

def multiMetrics_mult(models,train_or_test,printall=False,normalised=True):
    RMSE = 0
    timetable_RMSE = 0
    MAPE = 0
    timetable_MAPE = 0
    count = 0
    badroutes = dict()
    for model in models:
        X = model['X_'+train_or_test]
        y = model['y_'+train_or_test]
        y_max, y_min = model['max_trip'],model['min_trip']
        print(y_max)
        timetabled_values = model['timetabled_values_'+train_or_test]
        try:
            predictions = model['model'].predict(X)
        
        #   print(predictions_train/y_train)
    
            RMSE += metrics.mean_squared_error(y, predictions)**0.5
            timetable_RMSE += metrics.mean_squared_error(y, timetabled_values)**0.5

            MAPE += mean_absolute_percentage_error(y, predictions)
            timetable_MAPE += mean_absolute_percentage_error(y, timetabled_values)
        
            count += 1
            if printall == True:
                print(model['route'], model['direction'])
                if normalised:
                    printMetrics(y,predictions,timetabled_values)
                else:
                    printMetrics(unnormalise(y,y_max,y_min),unnormalise(predictions,y_max,y_min),unnormalise(timetabled_values,y_max,y_min))
                print("Training set size: ", X.size)
                    
            if metrics.mean_squared_error(y, predictions)**0.5 > metrics.mean_squared_error(y, timetabled_values)**0.5:
                badroutes[model['route'] + "_" + str(model['direction'])] = {
                    'training_size':X.size,
                    'mse_difference':metrics.mean_squared_error(y, predictions)**0.5 - metrics.mean_squared_error(y, timetabled_values)**0.5
                }
        except:
            pass
            
    print()
    print('Average model RMSE: ', RMSE/count)
    print('Average timetable RMSE: ', timetable_RMSE/count)
    print()
    print('Average model MAPE: ', MAPE/count)
    print('Average timetable MAPE: ', timetable_MAPE/count)
    print()
    print('Bad routes:' )
    print('---')
    for route in badroutes:
        print(route, '\t', badroutes[route]['training_size'], '\t', badroutes[route]['mse_difference'])
    print()
    print("Total bad routes: %s"%len(badroutes.keys()))

In [68]:
multiMetrics_mult(models_NN_test,'train',printall=True,normalised=False)

9416
66 1

MAE:  368.4922631714258
RMSE:  490.3517167386863
R2:  0.6060541471716129
MAPE:  8.471145148144698

MAE:  732.8563243465755
RMSE:  846.4072898280665
R2:  -0.17376166927810788
MAPE:  18.44730723668148
Training set size:  266076
8648
66 2

MAE:  318.8453795627395
RMSE:  429.7410040499753
R2:  0.6754514628390391
MAPE:  7.780622133848604

MAE:  424.6658235494145
RMSE:  545.822376300703
R2:  0.4764372510323469
MAPE:  10.866934036565773
Training set size:  227700
13531
77A 1

MAE:  429.27508050831517
RMSE:  575.856874500291
R2:  0.6439699526819066
MAPE:  10.26087145336544

MAE:  567.3955580844803
RMSE:  774.6244525298376
R2:  0.35577148325783114
MAPE:  12.542531103389825
Training set size:  359100
14153
77A 2

MAE:  383.9430320146672
RMSE:  522.7100268504831
R2:  0.6749882299786221
MAPE:  8.12395940394884

MAE:  1037.8772908535962
RMSE:  1172.7129934145805
R2:  -0.6359156269917845
MAPE:  24.261281618078133
Training set size:  392616
13579
41 2

MAE:  358.8530935285804
RMSE:  484.73

10271
7A 2

MAE:  366.7189223239425
RMSE:  481.9732111247867
R2:  0.7592496472231588
MAPE:  8.662814821960923

MAE:  834.0086501888668
RMSE:  967.3068086911208
R2:  0.030272701698946802
MAPE:  22.69892133383607
Training set size:  259632
8395
67 2

MAE:  341.7271057078122
RMSE:  458.0836852766599
R2:  0.5502111324824472
MAPE:  8.348023988014157

MAE:  510.83623173620583
RMSE:  669.3352619949236
R2:  0.03970102924766539
MAPE:  11.625712346109452
Training set size:  227196
12507
67 1

MAE:  330.0961442239862
RMSE:  437.979472780873
R2:  0.6568112046414107
MAPE:  7.472331652604455

MAE:  1347.2428890129593
RMSE:  1433.8802504347886
R2:  -2.678335625484913
MAPE:  33.05261111741446
Training set size:  268776
7620
7 2

MAE:  399.2419976433071
RMSE:  527.01495989055
R2:  0.7025836541424961
MAPE:  9.868189311029294

MAE:  453.41691919819175
RMSE:  601.1927477068301
R2:  0.6129684111833511
MAPE:  11.435244749718205
Training set size:  239652
11861
7 1

MAE:  531.0438896941292
RMSE:  761.1051590

R2:  0.5249489631892057
MAPE:  13.789429166141016
Training set size:  275724
16262
18 1

MAE:  427.0126839296859
RMSE:  583.6143636086477
R2:  0.5617998069909589
MAPE:  10.89098934695559

MAE:  686.1839414557514
RMSE:  831.8721345473609
R2:  0.10970532812888445
MAPE:  18.92307534768336
Training set size:  204084
13215
14 2

MAE:  505.1440125523458
RMSE:  729.4147449090066
R2:  0.5211803071906512
MAPE:  14.349069883483025

MAE:  493.36664258371223
RMSE:  621.9712004217889
R2:  0.6518523414517496
MAPE:  12.10596945886886
Training set size:  439740
9855
14 1

MAE:  407.57055424220584
RMSE:  561.1067475589792
R2:  0.5754463624971297
MAPE:  8.269812276177413

MAE:  821.3117262350341
RMSE:  947.2525266397031
R2:  -0.2099658925694512
MAPE:  18.294318388374933
Training set size:  426456
9224
25B 2

MAE:  311.0818589716616
RMSE:  425.7692137950927
R2:  0.6571955255652558
MAPE:  8.362117736763572

MAE:  939.0693403778635
RMSE:  1030.3392219438315
R2:  -1.0075133201891462
MAPE:  28.11119875383276

37 1

MAE:  362.6343072399238
RMSE:  478.7855316162536
R2:  0.6293732671686627
MAPE:  8.712577037506655

MAE:  775.9163633021718
RMSE:  887.729772845026
R2:  -0.27413743665877965
MAPE:  20.52994188214809
Training set size:  376488
10385
65B 1

MAE:  420.5030951695594
RMSE:  642.353045357013
R2:  0.5641244568625698
MAPE:  11.189631375826648

MAE:  470.9054955313802
RMSE:  710.5884526506427
R2:  0.4666022023477373
MAPE:  13.029269996291024
Training set size:  153432
9652
65B 2

MAE:  751.8257962652183
RMSE:  983.3091356304183
R2:  0.3681897929729365
MAPE:  17.606844791638878

MAE:  858.5663316933179
RMSE:  1099.5586800451874
R2:  0.20997049307553073
MAPE:  22.17462016365086
Training set size:  133668
9464
54A 2

MAE:  386.3576641045206
RMSE:  522.008920923299
R2:  0.5083006065120628
MAPE:  10.223619341060266

MAE:  739.5728541201478
RMSE:  871.9102425643083
R2:  -0.37178920691153805
MAPE:  21.63738648324313
Training set size:  202860
8442
54A 1

MAE:  295.99798281536346
RMSE:  425.071162

MAE:  259.8798915535805
RMSE:  340.6411978155869
R2:  0.6256090406308834
MAPE:  8.726420543757476

MAE:  313.1912865014893
RMSE:  403.10656696845234
R2:  0.47571098656761746
MAPE:  11.045396489445357
Training set size:  175320
10267
44 1

MAE:  438.17506862751793
RMSE:  578.0966267001647
R2:  0.6630926211440373
MAPE:  8.234972003966071

MAE:  636.7791475687192
RMSE:  782.2285166016367
R2:  0.3831537324395101
MAPE:  12.777126087757157
Training set size:  135756
10002
44 2

MAE:  499.5354333911545
RMSE:  662.8245270732959
R2:  0.7699127085465944
MAPE:  12.366444071608637

MAE:  535.6092753778222
RMSE:  680.4259265936887
R2:  0.7575304551575185
MAPE:  12.696654523461692
Training set size:  140508
4145
33B 1

MAE:  193.20826932255574
RMSE:  280.6648102936628
R2:  0.21257350094005123
MAPE:  14.013736968972998

MAE:  197.78510449735936
RMSE:  264.0305927771645
R2:  0.3031447138248031
MAPE:  13.364086280697093
Training set size:  165816
9748
33B 2

MAE:  321.87287513738465
RMSE:  503.97151912

Training set size:  159876
10278
184 1

MAE:  225.2720229406048
RMSE:  313.8148631758446
R2:  0.3694364557924914
MAPE:  8.441754398032021

MAE:  319.2535607035607
RMSE:  398.8792602718137
R2:  -0.018743267637951755
MAPE:  12.643480863737128
Training set size:  186480
6612
184 2

MAE:  362.5205375900653
RMSE:  487.48445465627157
R2:  0.3886019672096592
MAPE:  10.946840066550347

MAE:  725.2188688131747
RMSE:  786.1277044197238
R2:  -0.5899691522236041
MAPE:  24.671096002776036
Training set size:  179784
9995
84 1

MAE:  527.1687881973843
RMSE:  769.1752602130034
R2:  0.30493796866918255
MAPE:  12.486419593243065

MAE:  547.7962920772953
RMSE:  700.5002652012033
R2:  0.4235129457723483
MAPE:  12.30018655342725
Training set size:  134064
10226
84 2

MAE:  483.2620565596539
RMSE:  664.4919455350819
R2:  0.6628560289887131
MAPE:  12.071833709397572

MAE:  640.7376585326515
RMSE:  802.5730098425629
R2:  0.5081812784053097
MAPE:  16.518097675527038
Training set size:  132012
12122
69 1

MAE: 

41B 1

MAE:  341.78398092623195
RMSE:  458.0892333985692
R2:  0.5202148981290684
MAPE:  10.686583050623536

MAE:  945.2604033863786
RMSE:  1151.794282800903
R2:  -2.0331677248754767
MAPE:  32.793077066410774
Training set size:  34704
5296
41B 2

MAE:  323.2368199513768
RMSE:  426.5043723167739
R2:  0.4004005780412072
MAPE:  9.642893390716157

MAE:  679.4126259858201
RMSE:  804.7991028432593
R2:  -1.134957318986519
MAPE:  21.9915479213254
Training set size:  30312
5550
26 1

MAE:  216.8335636133228
RMSE:  300.16851485902924
R2:  0.5698985527999376
MAPE:  10.067507198251217

MAE:  510.7312301885655
RMSE:  573.4332733467912
R2:  -0.5696629568573282
MAPE:  26.718072215693965
Training set size:  172116
6068
26 2

MAE:  316.49840469969047
RMSE:  463.22476545012285
R2:  0.3356890379647134
MAPE:  15.970406573008496

MAE:  355.8165873212479
RMSE:  470.69519131203407
R2:  0.3140895779119788
MAPE:  18.518154749448485
Training set size:  158256
6216
40B 1

MAE:  250.52024646141234
RMSE:  334.90050

MAPE:  28.173643025639638
Training set size:  11628
6408
39X 2

MAE:  290.9508450056895
RMSE:  374.3384403987401
R2:  0.4913098374860133
MAPE:  7.001505984579275

MAE:  771.1629221058629
RMSE:  858.92667677593
R2:  -1.678160919989896
MAPE:  19.885973056760776
Training set size:  22248
9681
39X 1

MAE:  396.869566267634
RMSE:  550.9371498147307
R2:  0.28767346516765235
MAPE:  8.029466214121502

MAE:  1473.0438127702275
RMSE:  1573.2496424383428
R2:  -4.808584212105439
MAPE:  30.95341246816125
Training set size:  12600
5056
114 1

MAE:  196.1486920370118
RMSE:  263.56548451690566
R2:  0.6024654069656283
MAPE:  10.648338057234536

MAE:  537.2147197169026
RMSE:  595.2365066741067
R2:  -1.027575209435987
MAPE:  32.11846434066645
Training set size:  104436
8273
114 2

MAE:  231.79944098146274
RMSE:  323.8791688490098
R2:  0.49090872247478157
MAPE:  12.695704879962195

MAE:  600.8312542248387
RMSE:  667.2939967898094
R2:  -1.161046239761431
MAPE:  36.368742348724375
Training set size:  103320

R2:  0.18028869883571708
MAPE:  11.286670526521098

MAE:  515.7330257422425
RMSE:  565.7115790130537
R2:  -2.402282531001432
MAPE:  31.60930184345351
Training set size:  26820
4099
31D 2

MAE:  401.43530084820964
RMSE:  489.94397609631
R2:  0.07613300942824919
MAPE:  19.126800553482955

MAE:  703.8460882416393
RMSE:  810.4409361283458
R2:  -1.527896825733897
MAPE:  34.32143260975047
Training set size:  4356
4000
31D 1

MAE:  438.4024713111833
RMSE:  525.9029203674002
R2:  -1.5504985981110875
MAPE:  20.78416822010014

MAE:  653.360824
RMSE:  731.7648395430843
R2:  -3.9380672573015305
MAPE:  30.969988642065932
Training set size:  4500
6807
25D 2

MAE:  443.5528421353603
RMSE:  576.9411397691123
R2:  0.26171012039232167
MAPE:  11.723179799377103

MAE:  914.0245806247243
RMSE:  1037.798258345213
R2:  -1.3888549141414388
MAPE:  27.324314018764273
Training set size:  13824
6962
25D 1

MAE:  291.5842681758942
RMSE:  403.1758943747016
R2:  0.22274445529114162
MAPE:  8.191534084947737

MAE:  94

In [69]:
import mult_funcs 

test_train_dict = {}
        
# import warnings
# warnings.filterwarnings('ignore')

import time
time1 = time.time()


dfs2 = dict()
for line in dftrips['LINEID'].unique():
    for direction in dftrips[dftrips['LINEID'] == line]['DIRECTION'].unique():
        dfs2[line+'_'+str(direction)] = dftrips[dftrips['LINEID'] == line][dftrips['DIRECTION'] == direction]
dfs2_list = [item for item in dfs2.values()]
# models_NN_200_lbfgs = pool_process(mult_funcs.gen_NN_mult_200_lbfgs,dfs2_list,4)
models_NN_200_lbfgs = pool_process(mult_funcs.gen_NN_mult_500,dfs2_list,4)

print()
print("Seconds taken: ", time.time()-time1)

C:\Users\Mesel\Anaconda3\lib\site-packages\ipykernel_launcher.py:15: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  from ipykernel import kernelapp as app


No. Inputs: 252, pool_size: 4

Seconds taken:  111.08552312850952


In [70]:
multiMetrics_mult(models_NN_200_lbfgs,'train')

9416
8648
13531
14153
13579
9445
11430
8640
11027
6252
10181
14277
10201
8344
10188
13978
12552
12222
10323
10792
9422
10415
10804
11737
8858
10319
9224
10271
8395
12507
7620
11861
9073
6430
7195
8675
11668
13502
12888
9779
8660
7728
9270
10253
12335
12957
17375
10031
12815
11879
12138
14325
7332
12041
9912
16262
13215
9855
9224
7589
11321
4854
16040
12770
9314
10935
9600
8681
6160
6253
6356
6379
6540
6543
10651
10236
9189
8450
7647
7392
16011
8616
10385
9652
9464
8442
16083
9400
6873
6871
9112
9326
5144
5286
9768
7828
10100
7625
9548
16871
10955
7503
8865
8613
13861
13655
9911
10014
4817
5815
10267
10002
4145
9748
6204
6239
7341
8493
9444
7604
9662
9083
9752
11463
7071
7557
6589
6952
12644
23458
5444
6689
8546
3517
9862
9864
10278
6612
9995
10226
12122
9885
7596
7970
11008
8867
4787
7051
8947
5755
7007
8411
4552
9007
7893
6457
7816
4398
7846
10881
5880
5266
6825
5296
5550
6068
6216
5647
3726
5810
5916
5158
9814
7397
7379
7128
8830
7979
6499
6659
10569
7786
5691
10783
8848
10488
7237
7

In [71]:
multiMetrics_mult(models_NN_200_lbfgs,'test')

9416
8648
13531
14153
13579
9445
11430
8640
11027
6252
10181
14277
10201
8344
10188
13978
12552
12222
10323
10792
9422
10415
10804
11737
8858
10319
9224
10271
8395
12507
7620
11861
9073
6430
7195
8675
11668
13502
12888
9779
8660
7728
9270
10253
12335
12957
17375
10031
12815
11879
12138
14325
7332
12041
9912
16262
13215
9855
9224
7589
11321
4854
16040
12770
9314
10935
9600
8681
6160
6253
6356
6379
6540
6543
10651
10236
9189
8450
7647
7392
16011
8616
10385
9652
9464
8442
16083
9400
6873
6871
9112
9326
5144
5286
9768
7828
10100
7625
9548
16871
10955
7503
8865
8613
13861
13655
9911
10014
4817
5815
10267
10002
4145
9748
6204
6239
7341
8493
9444
7604
9662
9083
9752
11463
7071
7557
6589
6952
12644
23458
5444
6689
8546
3517
9862
9864
10278
6612
9995
10226
12122
9885
7596
7970
11008
8867
4787
7051
8947
5755
7007
8411
4552
9007
7893
6457
7816
4398
7846
10881
5880
5266
6825
5296
5550
6068
6216
5647
3726
5810
5916
5158
9814
7397
7379
7128
8830
7979
6499
6659
10569
7786
5691
10783
8848
10488
7237
7

In [72]:
dfs2_list[0]

LINEID DIRECTION  PLANNEDTIME_ARR  PLANNEDTIME_DEP  TRIPLENGTH MONTH  \
0           66         1            28733            25500        3777     1   
119         66         1            36533            33300        3160     1   
214         66         1            38933            35700        3388     1   
412         66         1            43044            39300        3200     1   
632         66         1            46644            42900        3240     1   
...        ...       ...              ...              ...         ...   ...   
1892862     66         1            74442            71100        4313    12   
1892965     66         1            76242            72900        3718    12   
1893072     66         1            78042            74700        3929    12   
1893157     66         1            79778            76500        3181    12   
1893229     66         1            81578            78300        3706    12   

        WEEKDAY WEEKEND RUSH_HOUR  PLANNEDTIME_DEP_COS  PLANNEDTIME_DEP_SIN  \
0             0   False      True            -0.279829             0.960050   
119           0   False     False            -0.751840             0.659346   
214           0   False     False            -0.854912             0.518773   
412           0   False     False            -0.960050             0.279829   
632           0   False     False            -0.999762             0.021815   
...         ...     ...       ...                  ...                  ...   
1892862       0   False     False             0.442289            -0.896873   
1892965       0   False     False             0.555570            -0.831470   
1893072       0   False     False             0.659346            -0.751840   
1893157       0   False     False             0.751840            -0.659346   
1893229       0   False     False             0.831470            -0.555570   

         feels_like weather_main  
0             -1.50       Clouds  
119           -2.98       Clouds  
214           -2.98       Clouds  
412           -3.49       Clouds  
632           -4.14       Clouds  
...             ...          ...  
1892862        5.78       Clouds  
1892965        5.52       Clouds  
1893072        5.52       Clouds  
1893157        4.87       Clouds  
1893229        4.87       Clouds  

[10559 rows x 13 columns]

### Tried lgbfs NN with 1000 iters

Performed very well on the training set (8.6% error) with little improvement on test set (12.46% error)

In [73]:
models_NN_200_lbfgs[0]

{'route': '66',
 'direction': 1,
 'model': MLPRegressor(activation='relu', alpha=0.0001, batch_size='auto', beta_1=0.9,
              beta_2=0.999, early_stopping=False, epsilon=1e-08,
              hidden_layer_sizes=(100,), learning_rate='constant',
              learning_rate_init=0.001, max_fun=15000, max_iter=500,
              momentum=0.9, n_iter_no_change=10, nesterovs_momentum=True,
              power_t=0.5, random_state=None, shuffle=True, solver='adam',
              tol=0.0001, validation_fraction=0.1, verbose=False,
              warm_start=False),
 'X_train':       PLANNEDTIME_DEP_COS  PLANNEDTIME_DEP_SIN  feels_like  MONTH_1  MONTH_2  \
 0               -0.537300             0.843391    0.235018        0        0   
 1                0.831470            -0.555570    0.690464        0        0   
 2               -0.980785             0.195090    0.309536        0        0   
 3               -0.173648             0.984808    0.280875        0        0   
 4             

In [74]:
time1 = time.time()

models_SVR_linear = pool_process(mult_funcs.gen_SVR_mult_linear,dfs2_list,4)

print()
print("Seconds taken: ", time.time()-time1)

No. Inputs: 252, pool_size: 4

Seconds taken:  129.4443006515503


In [75]:
multiMetrics_mult(models_SVR_linear,'train',printall=True,normalised=False) 

9416
66 1

MAE:  387.4449395210866
RMSE:  508.6886462042278
R2:  0.576039670052546
MAPE:  9.0222083147004

MAE:  732.8563243465755
RMSE:  846.4072898280665
R2:  -0.17376166927810788
MAPE:  18.44730723668148
Training set size:  266076
8648
66 2

MAE:  424.10816061030533
RMSE:  544.8482037953326
R2:  0.47830447122041087
MAPE:  10.771815231392887

MAE:  424.6658235494145
RMSE:  545.822376300703
R2:  0.4764372510323469
MAPE:  10.866934036565773
Training set size:  227700
13531
77A 1

MAE:  527.9862899365801
RMSE:  673.1223340264735
R2:  0.5135417852632969
MAPE:  12.891791191224328

MAE:  567.3955580844803
RMSE:  774.6244525298376
R2:  0.35577148325783114
MAPE:  12.542531103389825
Training set size:  359100
14153
77A 2

MAE:  515.0465529633848
RMSE:  661.8577207931054
R2:  0.4789172389197385
MAPE:  11.461829702979365

MAE:  1037.8772908535962
RMSE:  1172.7129934145805
R2:  -0.6359156269917845
MAPE:  24.261281618078133
Training set size:  392616
13579
41 2

MAE:  427.2667541126959
RMSE:  558

Training set size:  333180
9224
7A 1

MAE:  440.52943957201336
RMSE:  561.020536935653
R2:  0.5168054097600177
MAPE:  10.494376919280166

MAE:  472.15486059355237
RMSE:  596.5892425769927
R2:  0.4535940994767831
MAPE:  11.556554266830643
Training set size:  218016
10271
7A 2

MAE:  441.3798955765699
RMSE:  569.2576609928292
R2:  0.6641549899435764
MAPE:  10.745589710614471

MAE:  834.0086501888668
RMSE:  967.3068086911208
R2:  0.030272701698946802
MAPE:  22.69892133383607
Training set size:  259632
8395
67 2

MAE:  421.82662662505857
RMSE:  536.7281739600202
R2:  0.3825129714734775
MAPE:  10.650331410057076

MAE:  510.83623173620583
RMSE:  669.3352619949236
R2:  0.03970102924766539
MAPE:  11.625712346109452
Training set size:  227196
12507
67 1

MAE:  425.1558110717749
RMSE:  535.5365492157426
R2:  0.4868978681989854
MAPE:  10.09297557760108

MAE:  1347.2428890129593
RMSE:  1433.8802504347886
R2:  -2.678335625484913
MAPE:  33.05261111741446
Training set size:  268776
7620
7 2

MAE:  46

25A 2

MAE:  386.7816291364186
RMSE:  504.4128584534645
R2:  0.48230336666784657
MAPE:  11.459593312349066

MAE:  355.77511392767485
RMSE:  492.6554746883178
R2:  0.5061561278442104
MAPE:  10.118277445704518
Training set size:  341064
12041
25A 1

MAE:  363.22571459304476
RMSE:  448.49923043834826
R2:  0.47053569737389067
MAPE:  11.869354834590435

MAE:  989.0151559002632
RMSE:  1068.2481104512206
R2:  -2.003706862531167
MAPE:  33.204993003270644
Training set size:  334404
9912
18 2

MAE:  473.00453418349235
RMSE:  613.4445096690031
R2:  0.5731083825919564
MAPE:  15.12844966863994

MAE:  475.97553975704307
RMSE:  647.122656982154
R2:  0.5249489631892057
MAPE:  13.789429166141016
Training set size:  275724
16262
18 1

MAE:  637.2727093336855
RMSE:  785.0895933799684
R2:  0.207025791853092
MAPE:  17.359892504205547

MAE:  686.1839414557514
RMSE:  831.8721345473609
R2:  0.10970532812888445
MAPE:  18.92307534768336
Training set size:  204084
13215
14 2

MAE:  641.0010439457121
RMSE:  858.9

17A 2

MAE:  434.54716394142
RMSE:  559.9044856816156
R2:  0.4709138916350929
MAPE:  11.176078872754772

MAE:  372.8975001522572
RMSE:  517.2365525940592
R2:  0.5484801143737019
MAPE:  8.98607623510849
Training set size:  320868
7392
17A 1

MAE:  413.879245240851
RMSE:  525.6581169551131
R2:  0.5755112340011761
MAPE:  10.19963142665748

MAE:  443.3891540535902
RMSE:  550.6498721186699
R2:  0.534188145556694
MAPE:  11.519894269032745
Training set size:  354564
16011
37 2

MAE:  499.2988740339881
RMSE:  628.9366390906724
R2:  0.28220884435953086
MAPE:  13.346892864500544

MAE:  925.7369135821523
RMSE:  1022.6559642747518
R2:  -0.8977693262201643
MAPE:  25.42200877924749
Training set size:  208476
8616
37 1

MAE:  426.3108982799348
RMSE:  551.6799669145139
R2:  0.5079274569409903
MAPE:  10.43445432962059

MAE:  775.9163633021718
RMSE:  887.729772845026
R2:  -0.27413743665877965
MAPE:  20.52994188214809
Training set size:  376488
10385
65B 1

MAE:  529.5987833650986
RMSE:  729.437459472154

140 1

MAE:  460.3932261865961
RMSE:  574.0382532426056
R2:  0.09001656592444407
MAPE:  13.672623888370058

MAE:  601.3441366049954
RMSE:  697.9410406105042
R2:  -0.34520753410888894
MAPE:  18.345481962728336
Training set size:  535248
13655
140 2

MAE:  546.9871797099383
RMSE:  683.9820576890467
R2:  0.2578550859434401
MAPE:  16.34116760041502

MAE:  480.8071101082406
RMSE:  619.0340872070836
R2:  0.39210520460114584
MAPE:  13.121676990573366
Training set size:  481068
9911
47 1

MAE:  496.23637033699305
RMSE:  678.5402610130284
R2:  0.4695295708928342
MAPE:  15.483497740606445

MAE:  432.6863905680069
RMSE:  567.4717498328661
R2:  0.6289790538784585
MAPE:  13.447498198184643
Training set size:  140004
10014
47 2

MAE:  559.8748878713925
RMSE:  712.3921505750506
R2:  0.4386319860257394
MAPE:  15.270402224409507

MAE:  651.4627328125367
RMSE:  820.2565928866035
R2:  0.25576708798543735
MAPE:  18.40985459231974
Training set size:  86832
4817
32 2

MAE:  244.46589803831748
RMSE:  320.140

120 2

MAE:  280.70051232934486
RMSE:  402.97567823466153
R2:  0.34835163878120223
MAPE:  17.108454169520616

MAE:  399.1219867460472
RMSE:  445.45089224023815
R2:  0.20373925858269282
MAPE:  28.001483065768472
Training set size:  395136
6689
120 1

MAE:  319.0742011451222
RMSE:  437.16713345631354
R2:  0.31623790983663813
MAPE:  17.99709780798494

MAE:  319.6150270175637
RMSE:  376.1795802643935
R2:  0.49370872202520544
MAPE:  20.424503885384667
Training set size:  389988
8546
59 1

MAE:  276.2472752240152
RMSE:  354.97447991511046
R2:  -0.9559182064206093
MAPE:  25.50967438441587

MAE:  370.42566820584426
RMSE:  420.97400716377405
R2:  -1.7508505024150218
MAPE:  33.49158257837602
Training set size:  106416
3517
59 2

MAE:  160.01952239955511
RMSE:  207.20021507554497
R2:  0.3121711753750578
MAPE:  14.04121264855015

MAE:  325.6302540337383
RMSE:  357.62351343063415
R2:  -1.0490478440749844
MAPE:  30.199320306620386
Training set size:  106848
9862
70 2

MAE:  565.0078558643637
RMSE:  

26 1

MAE:  264.68599008421353
RMSE:  349.7487532002838
R2:  0.41608049717451334
MAPE:  12.76055938914094

MAE:  510.7312301885655
RMSE:  573.4332733467912
R2:  -0.5696629568573282
MAPE:  26.718072215693965
Training set size:  172116
6068
26 2

MAE:  348.7571125318559
RMSE:  501.7475382137699
R2:  0.22060362877003759
MAPE:  17.32121529413278

MAE:  355.8165873212479
RMSE:  470.69519131203407
R2:  0.3140895779119788
MAPE:  18.518154749448485
Training set size:  158256
6216
40B 1

MAE:  339.4846540182465
RMSE:  420.9707510536337
R2:  0.6650379961441955
MAPE:  18.01779120461539

MAE:  371.159645964303
RMSE:  506.3643887638661
R2:  0.5153613879412096
MAPE:  15.544202357601176
Training set size:  46188
5647
40B 2

MAE:  292.75895347443225
RMSE:  419.9872184283612
R2:  0.28451884156523954
MAPE:  10.592061846427889

MAE:  788.1324595263234
RMSE:  854.5378591437596
R2:  -1.9620246669399197
MAPE:  30.998385074345048
Training set size:  34128
3726
16C 2

MAE:  169.19288553138173
RMSE:  233.65012

MAE:  381.68319193290847
RMSE:  505.83132020098924
R2:  0.49608473010794896
MAPE:  7.000497184179934

MAE:  1129.0836458700364
RMSE:  1248.7871386477836
R2:  -2.0713048109982513
MAPE:  22.198716690643973
Training set size:  38304
9957
67X 1

MAE:  973.7747528588021
RMSE:  1167.5045504847703
R2:  0.21707492978538623
MAPE:  20.32039127261941

MAE:  989.3305212413376
RMSE:  1139.5016503922407
R2:  0.2541818413156549
MAPE:  21.259620669413735
Training set size:  33516
3075
236 1

MAE:  136.83621540357606
RMSE:  189.06105551402925
R2:  0.4472457748154578
MAPE:  6.665495976141054

MAE:  303.08576954129825
RMSE:  371.31424421444405
R2:  -1.1321174967920435
MAPE:  15.972993289804007
Training set size:  15588
4426
236 2

MAE:  212.97647894551932
RMSE:  319.8838301699464
R2:  0.3116248393596316
MAPE:  9.63761322143272

MAE:  553.9375488773767
RMSE:  631.0412610128476
R2:  -1.6788977006826187
MAPE:  28.173643025639638
Training set size:  11628
6408
39X 2

MAE:  268.3313087985452
RMSE:  352.459008

41X 2

MAE:  520.1350669991957
RMSE:  647.7895864216065
R2:  0.160950966871391
MAPE:  11.208873060149616

MAE:  710.6835218236113
RMSE:  809.5770466563249
R2:  -0.3104962717139943
MAPE:  16.399638432837104
Training set size:  31464
8521
41X 1

MAE:  443.77811910502925
RMSE:  561.2664557232316
R2:  0.2198995053453393
MAPE:  8.30973095118129

MAE:  556.3648715381331
RMSE:  689.2304350940827
R2:  -0.17636277297058456
MAPE:  10.814063607258035
Training set size:  21996
5444
44B 1

MAE:  244.2452370440454
RMSE:  322.19459971263524
R2:  0.30866970227299806
MAPE:  63.77846098699443

MAE:  289.4157796665144
RMSE:  421.4776960787163
R2:  -0.18303684655679842
MAPE:  91.84888177009594
Training set size:  27972
3686
44B 2

MAE:  200.3660095148865
RMSE:  275.65260222401923
R2:  0.19219891408779044
MAPE:  11.118497172093115

MAE:  515.7330257422425
RMSE:  565.7115790130537
R2:  -2.402282531001432
MAPE:  31.60930184345351
Training set size:  26820
4099
31D 2

MAE:  327.2581465466123
RMSE:  419.585224

In [76]:
multiMetrics_mult(models_SVR_linear,'test')

9416
8648
13531
14153
13579
9445
11430
8640
11027
6252
10181
14277
10201
8344
10188
13978
12552
12222
10323
10792
9422
10415
10804
11737
8858
10319
9224
10271
8395
12507
7620
11861
9073
6430
7195
8675
11668
13502
12888
9779
8660
7728
9270
10253
12335
12957
17375
10031
12815
11879
12138
14325
7332
12041
9912
16262
13215
9855
9224
7589
11321
4854
16040
12770
9314
10935
9600
8681
6160
6253
6356
6379
6540
6543
10651
10236
9189
8450
7647
7392
16011
8616
10385
9652
9464
8442
16083
9400
6873
6871
9112
9326
5144
5286
9768
7828
10100
7625
9548
16871
10955
7503
8865
8613
13861
13655
9911
10014
4817
5815
10267
10002
4145
9748
6204
6239
7341
8493
9444
7604
9662
9083
9752
11463
7071
7557
6589
6952
12644
23458
5444
6689
8546
3517
9862
9864
10278
6612
9995
10226
12122
9885
7596
7970
11008
8867
4787
7051
8947
5755
7007
8411
4552
9007
7893
6457
7816
4398
7846
10881
5880
5266
6825
5296
5550
6068
6216
5647
3726
5810
5916
5158
9814
7397
7379
7128
8830
7979
6499
6659
10569
7786
5691
10783
8848
10488
7237
7

In [164]:
time1 = time.time()

models_SVR = pool_process(mult_funcs.gen_SVR_mult,dfs2_list,4)

print()
print("Seconds taken: ", time.time()-time1)

No. Inputs: 252, pool_size: 4

Seconds taken:  47.42389798164368


In [165]:
multiMetrics_mult(models_SVR,'train',printall=True) 

9416
66 1

MAE:  0.046777326214377385
RMSE:  0.05970787180223142
R2:  0.6611150928217989
MAPE:  inf

MAE:  0.09621324988139365
RMSE:  0.1111208205104459
R2:  -0.17376166927810766
MAPE:  inf
Training set size:  266076
8648
66 2

MAE:  0.04629699741727035
RMSE:  0.057404167793770514
R2:  0.6613624616830487
MAPE:  inf

MAE:  0.055533650261463896
RMSE:  0.07137732134179457
R2:  0.4764372510323468
MAPE:  inf
Training set size:  227700
13531
77A 1

MAE:  0.03813519538801936
RMSE:  0.04762187243061188
R2:  0.5619513721529623
MAPE:  inf

MAE:  0.042301912926599586
RMSE:  0.057751767131129325
R2:  0.35577148325783114
MAPE:  inf
Training set size:  359100
14153
77A 2

MAE:  0.03806595505933521
RMSE:  0.048055736820982804
R2:  0.5860178007095715
MAPE:  inf

MAE:  0.08454523385904171
RMSE:  0.0955289176779554
R2:  -0.6359156269917845
MAPE:  inf
Training set size:  392616
13579
41 2

MAE:  0.03530118451475265
RMSE:  0.04476559326418663
R2:  0.3237198759109772
MAPE:  inf

MAE:  0.0683859779237865
RM

7A 2

MAE:  0.044834160727708176
RMSE:  0.05702270471542645
R2:  0.7608025325702359
MAPE:  inf

MAE:  0.09899212465149752
RMSE:  0.11481386453307071
R2:  0.030272701698946913
MAPE:  inf
Training set size:  259632
8395
67 2

MAE:  0.04691313780018313
RMSE:  0.0578049360585584
R2:  0.5033779107382848
MAPE:  10.311596515693006

MAE:  0.061346971506689774
RMSE:  0.0803813212435359
R2:  0.039701029247665276
MAPE:  11.964382436894292
Training set size:  227196
12507
67 1

MAE:  0.04072007226263548
RMSE:  0.049968764712371175
R2:  0.5481859685077759
MAPE:  inf

MAE:  0.13396071283811864
RMSE:  0.14257534557370874
R2:  -2.678335625484913
MAPE:  inf
Training set size:  268776
7620
7 2

MAE:  0.05955344285014794
RMSE:  0.07394066685099497
R2:  0.710256383566179
MAPE:  12.839191176327603

MAE:  0.0644515876614345
RMSE:  0.08545739128739589
R2:  0.6129684111833512
MAPE:  13.708928509804426
Training set size:  239652
11861
7 1

MAE:  0.05693299329369742
RMSE:  0.07813569652353519
R2:  0.44436016559

14 2

MAE:  0.04652374587466477
RMSE:  0.06167137597224017
R2:  0.472425675521578
MAPE:  25.836272053782842

MAE:  0.03973956041753623
RMSE:  0.05009836491516624
R2:  0.6518523414517496
MAPE:  18.479557955474217
Training set size:  439740
9855
14 1

MAE:  0.05291367416658
RMSE:  0.06991158392304059
R2:  0.585222895588608
MAPE:  15.40005349263502

MAE:  0.10353103822450951
RMSE:  0.11940659607206644
R2:  -0.2099658925694512
MAPE:  33.64143104889478
Training set size:  426456
9224
25B 2

MAE:  0.04581809848701364
RMSE:  0.058625815953433094
R2:  0.6444754656966473
MAPE:  inf

MAE:  0.12696989458867813
RMSE:  0.13931033287504482
R2:  -1.007513320189147
MAPE:  inf
Training set size:  277776
7589
25B 1

MAE:  0.041904761242640434
RMSE:  0.05247616933456039
R2:  0.6037220323474435
MAPE:  inf

MAE:  0.045741490399024635
RMSE:  0.061150814881196724
R2:  0.4618787097697147
MAPE:  inf
Training set size:  315144
11321
27A 1

MAE:  0.04396867691488436
RMSE:  0.05097103069724854
R2:  -0.55292106504

54A 2

MAE:  0.053430334032325826
RMSE:  0.0683866686932984
R2:  0.5018634758129863
MAPE:  inf

MAE:  0.0962609467812245
RMSE:  0.11348564916885438
R2:  -0.37178920691153783
MAPE:  inf
Training set size:  202860
8442
54A 1

MAE:  0.04296397832429537
RMSE:  0.055259758372014765
R2:  0.46732367946193065
MAPE:  12.202643688779672

MAE:  0.04328514839257049
RMSE:  0.061555728633191545
R2:  0.33902903726330846
MAPE:  11.268897424037387
Training set size:  225720
16083
9 1

MAE:  0.03262391275316167
RMSE:  0.041287402224810824
R2:  0.5107540503612491
MAPE:  inf

MAE:  0.036011251269712885
RMSE:  0.04435833564839894
R2:  0.43526772596952834
MAPE:  inf
Training set size:  485748
9400
9 2

MAE:  0.049156185399390456
RMSE:  0.06291757392737289
R2:  0.6519016927765906
MAPE:  inf

MAE:  0.060242677247261296
RMSE:  0.07531610898602821
R2:  0.5011916377107479
MAPE:  inf
Training set size:  505764
6873
15A 1

MAE:  0.04178837026375812
RMSE:  0.05253287471015322
R2:  0.6499542659324467
MAPE:  inf

MAE

44 2

MAE:  0.05819027062503258
RMSE:  0.07005690049506104
R2:  0.792631192597454
MAPE:  36.16145292602892

MAE:  0.059631404517682285
RMSE:  0.07575438951165539
R2:  0.7575304551575185
MAPE:  34.35868157414112
Training set size:  140508
4145
33B 1

MAE:  0.05379544803085475
RMSE:  0.06988750742533865
R2:  0.27705821530000674
MAPE:  inf

MAE:  0.05139945543070669
RMSE:  0.06861501891298455
R2:  0.303144713824803
MAPE:  inf
Training set size:  165816
9748
33B 2

MAE:  0.04121695693675226
RMSE:  0.05915814690499451
R2:  0.03499734838006996
MAPE:  32.19269713400377

MAE:  0.03677196645237272
RMSE:  0.058433642634216784
R2:  0.0584892045481995
MAPE:  24.873022247817374
Training set size:  123480
6204
43 2

MAE:  0.047148431857703614
RMSE:  0.05850756918699551
R2:  0.5623926482615649
MAPE:  10.279703087567842

MAE:  0.05388671122124306
RMSE:  0.0718931653488048
R2:  0.33925222328637183
MAPE:  10.849663003690198
Training set size:  186768
6239
43 1

MAE:  0.052626776065486644
RMSE:  0.066205

84 2

MAE:  0.05582435199593358
RMSE:  0.07308979052237005
R2:  0.6821840836270747
MAPE:  inf

MAE:  0.072588383202974
RMSE:  0.09092251159426337
R2:  0.5081812784053097
MAPE:  inf
Training set size:  132012
12122
69 1

MAE:  0.0438264295275141
RMSE:  0.05285568829796741
R2:  0.0996902683118942
MAPE:  inf

MAE:  0.033180472336924
RMSE:  0.04918840371380947
R2:  0.22028850497212316
MAPE:  inf
Training set size:  134964
9885
69 2

MAE:  0.04669136838662078
RMSE:  0.059850195859509396
R2:  0.6964430258372025
MAPE:  inf

MAE:  0.08078476955486646
RMSE:  0.09589209476973988
R2:  0.22075383238694235
MAPE:  inf
Training set size:  129312
7596
17 2

MAE:  0.06225047846290578
RMSE:  0.0810568643877579
R2:  0.7040034611608659
MAPE:  inf

MAE:  0.11067577629869751
RMSE:  0.13230613839773492
R2:  0.21138138942640983
MAPE:  inf
Training set size:  202428
7970
17 1

MAE:  0.060692655127489475
RMSE:  0.08593604130831564
R2:  0.5713241242802694
MAPE:  29.92040436097468

MAE:  0.057795765595421246
RMSE

66B 2

MAE:  0.05543967153889993
RMSE:  0.0690042315143685
R2:  0.6411298206798907
MAPE:  inf

MAE:  0.1350002403306721
RMSE:  0.14984886930836971
R2:  -0.6923604409764459
MAPE:  inf
Training set size:  107064
7379
38B 2

MAE:  0.08606350991045575
RMSE:  0.1044210859715013
R2:  0.6860392603458937
MAPE:  inf

MAE:  0.11377435886019227
RMSE:  0.1345835570257469
R2:  0.4784656264193795
MAPE:  inf
Training set size:  38988
7128
38B 1

MAE:  0.0764445984765341
RMSE:  0.09056002841976127
R2:  0.515974235910343
MAPE:  inf

MAE:  0.20337073926350432
RMSE:  0.23068905036001422
R2:  -2.140865516397182
MAPE:  inf
Training set size:  25020
8830
84A 2

MAE:  0.04711691856698431
RMSE:  0.06982449782547534
R2:  0.3891973897431573
MAPE:  36.45312455218699

MAE:  0.14288674465282045
RMSE:  0.15511298608625032
R2:  -2.014265893454238
MAPE:  133.52939245252276
Training set size:  43092
7979
84A 1

MAE:  0.06499611011996642
RMSE:  0.09901881239851576
R2:  0.3556946664519137
MAPE:  inf

MAE:  0.13221845786

77X 2

MAE:  0.08375181066149597
RMSE:  0.10413366036045618
R2:  0.5747311856527257
MAPE:  16.053041513898787

MAE:  0.17868956045203493
RMSE:  0.21259864755796182
R2:  -0.7725653786251261
MAPE:  38.62020402405419
Training set size:  5364
9033
66X 2

MAE:  0.07313702426952708
RMSE:  0.09148370341246323
R2:  0.4035129236559971
MAPE:  inf

MAE:  0.16894211654337798
RMSE:  0.18935392978582707
R2:  -1.5554195297047384
MAPE:  inf
Training set size:  45504
8770
66X 1

MAE:  0.15807969299340746
RMSE:  0.18217101508558706
R2:  0.12131860481993517
MAPE:  inf

MAE:  0.16935657967128834
RMSE:  0.19267045891161289
R2:  0.01711402525401995
MAPE:  inf
Training set size:  33228
9159
142 1

MAE:  0.04776028676464833
RMSE:  0.05529492167242891
R2:  0.9629767243678968
MAPE:  inf

MAE:  0.05855859325556102
RMSE:  0.0681544775045869
R2:  0.9437538071880487
MAPE:  inf
Training set size:  48996
8486
142 2

MAE:  0.05429853365825128
RMSE:  0.06122413196655697
R2:  0.9578213519720701
MAPE:  inf

MAE:  0.05991

MAPE:  124.60747159956698
Training set size:  1152
4821
33D 2

MAE:  0.09412814318523567
RMSE:  0.11474928387627523
R2:  0.6125434560494722
MAPE:  inf

MAE:  0.21283309864024083
RMSE:  0.24719512663220508
R2:  -0.7980544598761288
MAPE:  inf
Training set size:  2556
4529
33D 1

MAE:  0.08510278171978405
RMSE:  0.10446138829270017
R2:  0.4253945586170296
MAPE:  inf

MAE:  0.3531907185442601
RMSE:  0.37977830273410995
R2:  -6.594836803015296
MAPE:  inf
Training set size:  3420
3333
40E 1

MAE:  0.09358849292996503
RMSE:  0.12939014906239923
R2:  0.2626033595012126
MAPE:  38.69342935302617

MAE:  0.3590463235179862
RMSE:  0.37759961121949565
R2:  -5.280031255908629
MAPE:  192.18508304682967
Training set size:  12096
3828
40E 2

MAE:  0.0651643315180677
RMSE:  0.093410557682517
R2:  0.4846005531591516
MAPE:  inf

MAE:  0.1980721738178882
RMSE:  0.2123731318348287
R2:  -1.664103918958559
MAPE:  inf
Training set size:  14436
6950
33E 1

MAE:  0.14913507623201477
RMSE:  0.1675258432432354
R2: 

In [166]:
multiMetrics_mult(models_SVR,'test',printall=True) 

9416
66 1

MAE:  0.04929348994946539
RMSE:  0.06441964595331567
R2:  0.6150347074989263
MAPE:  15.965736132258643

MAE:  0.09790810558239944
RMSE:  0.11274856703018793
R2:  -0.1792529491095709
MAPE:  35.73951947314073
Training set size:  114048
8648
66 2

MAE:  0.04924745790324741
RMSE:  0.06311991709486081
R2:  0.568406651864831
MAPE:  13.379215984652019

MAE:  0.05435277724987438
RMSE:  0.06919509929100827
R2:  0.48132827103653375
MAPE:  14.874871736128693
Training set size:  97632
13531
77A 1

MAE:  0.0381403771011858
RMSE:  0.04789204139753938
R2:  0.557496167977189
MAPE:  11.75002704529358

MAE:  0.04264095477755587
RMSE:  0.0578567514712681
R2:  0.3541994238185312
MAPE:  11.866261310805818
Training set size:  153900
14153
77A 2

MAE:  0.038532596781708305
RMSE:  0.049048731854483295
R2:  0.5591379144382986
MAPE:  20.048193803348692

MAE:  0.08446545961709591
RMSE:  0.09519766455602581
R2:  -0.6607328359148186
MAPE:  47.232160962931424
Training set size:  168264
13579
41 2

MAE:  

R2:  0.5616278729483628
MAPE:  12.559158389972398

MAE:  0.056837087697975505
RMSE:  0.07227639276642074
R2:  0.4471554009544777
MAPE:  14.852696163960353
Training set size:  93456
10271
7A 2

MAE:  0.047562355533671934
RMSE:  0.06059015036451047
R2:  0.7326973352719249
MAPE:  22.61380303561981

MAE:  0.09757512776573615
RMSE:  0.11394847102507541
R2:  0.05459861985700265
MAPE:  63.367908206546964
Training set size:  111276
8395
67 2

MAE:  0.04787843603415772
RMSE:  0.06120025600986338
R2:  0.4648648337732373
MAPE:  inf

MAE:  0.061646088383268516
RMSE:  0.081038720754645
R2:  0.06169902566357954
MAPE:  inf
Training set size:  97380
12507
67 1

MAE:  0.04206027167459178
RMSE:  0.053978985822373406
R2:  0.48660318233703237
MAPE:  29.12187378115268

MAE:  0.13433113800112048
RMSE:  0.1429961048375295
R2:  -2.602899486070359
MAPE:  93.7141810007864
Training set size:  115200
7620
7 2

MAE:  0.06093686235631738
RMSE:  0.07912936576753174
R2:  0.6680671554292867
MAPE:  inf

MAE:  0.0639617

R2:  0.4429834192195249
MAPE:  inf

MAE:  0.09546212963641117
RMSE:  0.10335602188285883
R2:  -1.8218581877243718
MAPE:  inf
Training set size:  143352
9912
18 2

MAE:  0.04382741168650262
RMSE:  0.056449152514235615
R2:  0.6394302350818484
MAPE:  11.54325063325791

MAE:  0.04898792371947081
RMSE:  0.06600027025961622
R2:  0.5070919825359147
MAPE:  11.57841335922169
Training set size:  118188
16262
18 1

MAE:  0.04297318895739
RMSE:  0.05051286648267594
R2:  0.17563642270272983
MAPE:  inf

MAE:  0.04415445276774851
RMSE:  0.05280786458781636
R2:  0.09902658042908274
MAPE:  inf
Training set size:  87480
13215
14 2

MAE:  0.047446044995017575
RMSE:  0.06551288041049858
R2:  0.4246586536287291
MAPE:  inf

MAE:  0.03933399933762836
RMSE:  0.04999750822793751
R2:  0.6649042518307324
MAPE:  inf
Training set size:  188460
9855
14 1

MAE:  0.055704947060172816
RMSE:  0.07498644855787527
R2:  0.5260472662371714
MAPE:  inf

MAE:  0.10313343043405082
RMSE:  0.11985742495222712
R2:  -0.21087509753

37 1

MAE:  0.056983758169335236
RMSE:  0.07352349920912844
R2:  0.5974914895276415
MAPE:  19.810954282735842

MAE:  0.11674029290231777
RMSE:  0.13303691463162587
R2:  -0.317853272282526
MAPE:  46.29550712938631
Training set size:  161352
10385
65B 1

MAE:  0.058317057974002405
RMSE:  0.08049227317024436
R2:  0.4136135933173746
MAPE:  19.686371408389856

MAE:  0.050545968295974915
RMSE:  0.07806270413492916
R2:  0.4484781889904369
MAPE:  16.698259087884548
Training set size:  65772
9652
65B 2

MAE:  0.0990564304315366
RMSE:  0.12944602547930517
R2:  0.3440388534654918
MAPE:  43.24094668257994

MAE:  0.10997505362152137
RMSE:  0.14023504264284542
R2:  0.23013641566802656
MAPE:  61.416392120251174
Training set size:  57312
9464
54A 2

MAE:  0.054522406508868006
RMSE:  0.07183677594829332
R2:  0.4353572216082311
MAPE:  26.064729602369564

MAE:  0.09702241812563625
RMSE:  0.11361044935063935
R2:  -0.41226653243703826
MAPE:  53.185962111031614
Training set size:  86940
8442
54A 1

MAE:  0.

MAE:  0.06295200405765322
RMSE:  0.08204547713801012
R2:  0.6435185238047048
MAPE:  inf

MAE:  0.15928919830091615
RMSE:  0.18035245727250765
R2:  -0.7225498747454191
MAPE:  inf
Training set size:  75240
5815
32 1

MAE:  0.05175725108718892
RMSE:  0.06700844928741378
R2:  0.5943974840714497
MAPE:  11.494406493194374

MAE:  0.059556801715930405
RMSE:  0.07581036786517709
R2:  0.4808430012340018
MAPE:  13.81193535648903
Training set size:  75168
10267
44 1

MAE:  0.05024478094830273
RMSE:  0.0661856037016994
R2:  0.6652485481893939
MAPE:  11.761582094718271

MAE:  0.07170952062752523
RMSE:  0.08899980289101493
R2:  0.39469607546183494
MAPE:  18.58421622515658
Training set size:  58212
10002
44 2

MAE:  0.061490942495021204
RMSE:  0.07644602717686766
R2:  0.7348189211574306
MAPE:  inf

MAE:  0.059316079886476115
RMSE:  0.07746619178551607
R2:  0.7276940659226698
MAPE:  inf
Training set size:  60264
4145
33B 1

MAE:  0.058365909146328256
RMSE:  0.07766632312084708
R2:  0.12865044423573502


MAE:  0.06368111078293838
RMSE:  0.07842507696291391
R2:  0.54615637951238
MAPE:  28.80278709780925

MAE:  0.13179533689001444
RMSE:  0.15230245621705563
R2:  -0.7116309965997307
MAPE:  73.2642888581931
Training set size:  68544
10278
184 1

MAE:  0.040088243736553675
RMSE:  0.04741172774047344
R2:  -0.4790233887577431
MAPE:  19.73428287773743

MAE:  0.03230390429576584
RMSE:  0.039119040710597644
R2:  -0.0068849996226727495
MAPE:  16.06673449684881
Training set size:  79920
6612
184 2

MAE:  0.0860844966096701
RMSE:  0.109661555585848
R2:  0.28977143270015326
MAPE:  inf

MAE:  0.14920935252074727
RMSE:  0.161343766205923
R2:  -0.5374242008842822
MAPE:  inf
Training set size:  77076
9995
84 1

MAE:  0.07123341559750908
RMSE:  0.09845455851439971
R2:  0.13900687229862796
MAPE:  27.05235595016053

MAE:  0.06257272026298506
RMSE:  0.07753759590571739
R2:  0.46598594260901294
MAPE:  23.35624759794949
Training set size:  57492
10226
84 2

MAE:  0.060026026495933804
RMSE:  0.0796783739493906

26 1

MAE:  0.055889921912952265
RMSE:  0.07177369217277604
R2:  0.4382605168600211
MAPE:  inf

MAE:  0.11116984972698082
RMSE:  0.12492643541207522
R2:  -0.7018178371984338
MAPE:  inf
Training set size:  73764
6068
26 2

MAE:  0.06221810614962971
RMSE:  0.08772260552291085
R2:  0.3005236773897292
MAPE:  inf

MAE:  0.06717968941103582
RMSE:  0.08704155958620267
R2:  0.3113424692550284
MAPE:  inf
Training set size:  67860
6216
40B 1

MAE:  0.05403869810910186
RMSE:  0.06762827433358169
R2:  0.6698912944021018
MAPE:  18.34526611799857

MAE:  0.06189049603239796
RMSE:  0.08485264186249679
R2:  0.4803258633149248
MAPE:  15.517094484721364
Training set size:  19800
5647
40B 2

MAE:  0.06908691511370257
RMSE:  0.10084194124727984
R2:  0.3231029374552479
MAPE:  inf

MAE:  0.20712327630596664
RMSE:  0.22142653207685828
R2:  -2.263619739156588
MAPE:  inf
Training set size:  14652
3726
16C 2

MAE:  0.08190970590684671
RMSE:  0.10413402257040259
R2:  0.5852377696597826
MAPE:  42.497211836007075



39X 1

MAE:  0.05875856737361184
RMSE:  0.07851391044853157
R2:  0.3603682162583215
MAPE:  28.203273600087126

MAE:  0.23639784171692985
RMSE:  0.24960900837323138
R2:  -5.464833278385935
MAPE:  126.00451956753453
Training set size:  5400
5056
114 1

MAE:  0.05227279565636875
RMSE:  0.06585880811112323
R2:  0.5545569968416477
MAPE:  37.79275904477854

MAE:  0.1325520293442696
RMSE:  0.1449905705531881
R2:  -1.1589566682288224
MAPE:  105.55461755454844
Training set size:  44784
8273
114 2

MAE:  0.04564846553799053
RMSE:  0.05758129565517056
R2:  0.23296766170535543
MAPE:  56.31686450878794

MAE:  0.08369401332880971
RMSE:  0.09213320006520549
R2:  -0.9637360828647656
MAPE:  104.25634913078447
Training set size:  44316
4707
70D 2

MAE:  0.11831822711527584
RMSE:  0.15284410246345168
R2:  0.24647611005262215
MAPE:  inf

MAE:  0.32920147489858476
RMSE:  0.3663674483668197
R2:  -3.3294568288276274
MAPE:  inf
Training set size:  1512
6132
70D 1

MAE:  0.12342358277864096
RMSE:  0.1703783942

RMSE:  0.2582892709109656
R2:  -0.6021822054702535
MAPE:  66.83780993696661
Training set size:  1728
5747
15D 1

MAE:  0.0911263251106938
RMSE:  0.12709701038707719
R2:  0.28643454176092886
MAPE:  inf

MAE:  0.22896254526110216
RMSE:  0.26042520231637784
R2:  -1.995912804613536
MAPE:  inf
Training set size:  4176
6865
25X 2

MAE:  0.10830355935793075
RMSE:  0.1419205575653111
R2:  0.07252590275333748
MAPE:  46.82948924034747

MAE:  0.3042559849708333
RMSE:  0.3238441671761059
R2:  -3.829290498805558
MAPE:  156.1535334310538
Training set size:  2124
8082
25X 1

MAE:  0.08588402384135611
RMSE:  0.12863911661520938
R2:  0.11140603828830054
MAPE:  29.73851031644829

MAE:  0.23863286609791853
RMSE:  0.2623127143210377
R2:  -2.6948426018657234
MAPE:  96.54320914887433
Training set size:  4140
4080
68A 2

MAE:  0.11544660788397124
RMSE:  0.14397753012950984
R2:  0.3498660352439471
MAPE:  33.789754626131135

MAE:  0.16065248927492018
RMSE:  0.18713847809414172
R2:  -0.09834708947601056
MAPE:  

In [176]:
models_SVR_noDFs = list()
for model in models_SVR:
    models_SVR_noDFs += [{key:model[key] for key in model}]

In [177]:
for model in models_SVR_noDFs:
    model['columns'] = model['X_train'].columns
    model.pop('X_train')
    model.pop('X_test')
    model.pop('y_train')
    model.pop('y_test')
    model.pop('timetabled_values_train')
    model.pop('timetabled_values_test')

In [178]:
models_SVR_noDFs

[{'route': '66',
  'direction': 1,
  'model': SVR(C=1.0, cache_size=200, coef0=0.0, degree=3, epsilon=0.1, gamma='scale',
      kernel='rbf', max_iter=-1, shrinking=True, tol=0.001, verbose=False),
  'max_trip': 9416,
  'min_trip': 1799,
  'max_feels_like': 24.77,
  'min_feels_like': -13.61,
  'columns': Index(['PLANNEDTIME_DEP_COS', 'PLANNEDTIME_DEP_SIN', 'feels_like', 'MONTH_1',
         'MONTH_2', 'MONTH_3', 'MONTH_4', 'MONTH_5', 'MONTH_6', 'MONTH_7',
         'MONTH_8', 'MONTH_9', 'MONTH_10', 'MONTH_11', 'MONTH_12', 'WEEKDAY_0',
         'WEEKDAY_1', 'WEEKDAY_2', 'WEEKDAY_3', 'WEEKDAY_4', 'WEEKDAY_5',
         'WEEKDAY_6', 'WEEKEND_False', 'WEEKEND_True', 'RUSH_HOUR_False',
         'RUSH_HOUR_True', 'weather_main_Clear', 'weather_main_Clouds',
         'weather_main_Drizzle', 'weather_main_Fog', 'weather_main_Haze',
         'weather_main_Mist', 'weather_main_Rain', 'weather_main_Smoke',
         'weather_main_Snow', 'weather_main_Thunderstorm'],
        dtype='object')},
 {'route

In [172]:
models_SVR

[{'route': '66',
  'direction': 1,
  'model': SVR(C=1.0, cache_size=200, coef0=0.0, degree=3, epsilon=0.1, gamma='scale',
      kernel='rbf', max_iter=-1, shrinking=True, tol=0.001, verbose=False),
  'X_train':       PLANNEDTIME_DEP_COS  PLANNEDTIME_DEP_SIN  feels_like  MONTH_1  MONTH_2  \
  0               -0.537300             0.843391    0.235018        0        0   
  1                0.831470            -0.555570    0.690464        0        0   
  2               -0.980785             0.195090    0.309536        0        0   
  3               -0.173648             0.984808    0.280875        0        0   
  4               -0.751840             0.659346    0.699062        0        0   
  ...                   ...                  ...         ...      ...      ...   
  7386            -0.043619             0.999048    0.383273        0        0   
  7387            -0.422618             0.906308    0.558885        0        0   
  7388            -0.751840             0.659346    0

In [179]:
mname = 'models_SVR/models.pkl'
pickle.dump(models_SVR_noDFs,open(mname,'wb'))

In [81]:
time1 = time.time()

models_LR = pool_process(mult_funcs.gen_LR_mult,dfs2_list,4)

print()
print("Seconds taken: ", time.time()-time1)

No. Inputs: 252, pool_size: 4

Seconds taken:  9.667123317718506


In [82]:
multiMetrics_mult(models_LR,'train',printall=True) 

9416
66 1

MAE:  0.04957337409425528
RMSE:  0.0661590335931734
R2:  0.5839290933184176
MAPE:  inf

MAE:  0.09621324988139365
RMSE:  0.1111208205104459
R2:  -0.17376166927810766
MAPE:  inf
Training set size:  266076
8648
66 2

MAE:  0.052165939957459016
RMSE:  0.0695820640708187
R2:  0.5024429744820064
MAPE:  inf

MAE:  0.055533650261463896
RMSE:  0.07137732134179457
R2:  0.4764372510323468
MAPE:  inf
Training set size:  227700
13531
77A 1

MAE:  0.03595055112677054
RMSE:  0.04773205724356801
R2:  0.5599219624891932
MAPE:  inf

MAE:  0.042301912926599586
RMSE:  0.057751767131129325
R2:  0.35577148325783114
MAPE:  inf
Training set size:  359100
14153
77A 2

MAE:  0.038466504649582726
RMSE:  0.05155626699764836
R2:  0.5235096444967705
MAPE:  inf

MAE:  0.08454523385904171
RMSE:  0.0955289176779554
R2:  -0.6359156269917845
MAPE:  inf
Training set size:  392616
13579
41 2

MAE:  0.03054375423829209
RMSE:  0.04194676535994558
R2:  0.4062072533842832
MAPE:  inf

MAE:  0.0683859779237865
RMSE:

MAE:  0.05770245738777056
RMSE:  0.08289568868393683
R2:  0.3745994119756112
MAPE:  inf

MAE:  0.10998678546630404
RMSE:  0.12982239516679892
R2:  -0.5338879375518375
MAPE:  inf
Training set size:  210816
9073
29A 2

MAE:  0.03307369722885202
RMSE:  0.04528767827856896
R2:  0.4895230355961945
MAPE:  inf

MAE:  0.08398113142242396
RMSE:  0.09239790649584918
R2:  -1.1249088157682312
MAPE:  inf
Training set size:  383364
6430
29A 1

MAE:  0.047727006898323286
RMSE:  0.062373854942993696
R2:  0.5147028937824305
MAPE:  inf

MAE:  0.1319946608620719
RMSE:  0.14385716220689515
R2:  -1.5814606401401878
MAPE:  inf
Training set size:  329184
7195
123 2

MAE:  0.05548801495314594
RMSE:  0.07319932407490798
R2:  0.42244172033996075
MAPE:  inf

MAE:  0.054018090562767615
RMSE:  0.070139361022055
R2:  0.4697199571259737
MAPE:  inf
Training set size:  542124
8675
123 1

MAE:  0.04894108837844588
RMSE:  0.06382589716670596
R2:  0.4907556746129338
MAPE:  inf

MAE:  0.0674954494161243
RMSE:  0.080267649

RMSE:  0.0477083730620305
R2:  0.5582077336961637
MAPE:  inf
Training set size:  698112
9314
39A 2

MAE:  0.06401908524593129
RMSE:  0.08345757469876479
R2:  0.48427704248843917
MAPE:  inf

MAE:  0.08020698172172536
RMSE:  0.09595631410028686
R2:  0.3182391479454957
MAPE:  inf
Training set size:  618660
10935
39A 1

MAE:  0.050265894277501826
RMSE:  0.06786049740615677
R2:  0.5583901370993625
MAPE:  inf

MAE:  0.05028748805185139
RMSE:  0.06629401870370308
R2:  0.578542894593483
MAPE:  inf
Training set size:  538488
9600
15B 2

MAE:  0.054493806683965786
RMSE:  0.07421734223486076
R2:  0.450123059667634
MAPE:  inf

MAE:  0.09617031703561266
RMSE:  0.10973564741457337
R2:  -0.20212650286375
MAPE:  inf
Training set size:  400572
8681
15B 1

MAE:  0.05456450690731702
RMSE:  0.06911677901714058
R2:  0.36246047857068453
MAPE:  inf

MAE:  0.05564707788857245
RMSE:  0.07574176142346417
R2:  0.23438412200833791
MAPE:  inf
Training set size:  397944
6160
31 1

MAE:  0.04778953441898895
RMSE:  0

MAPE:  inf

MAE:  0.07032198194507852
RMSE:  0.0768855322683889
R2:  -1.8518210266542487
MAPE:  inf
Training set size:  120204
10955
76 1

MAE:  0.03569962536514435
RMSE:  0.047625767713345986
R2:  0.5221979451344789
MAPE:  inf

MAE:  0.03734735057956803
RMSE:  0.0492251065207744
R2:  0.489568622742673
MAPE:  inf
Training set size:  279036
7503
76 2

MAE:  0.03887001498331724
RMSE:  0.05366196658017251
R2:  0.5912905882730641
MAPE:  inf

MAE:  0.07852082557813603
RMSE:  0.09011076051030825
R2:  -0.15248366855076267
MAPE:  inf
Training set size:  245340
8865
49 2

MAE:  0.07433076967406249
RMSE:  0.10425075736993042
R2:  0.15220377541778385
MAPE:  inf

MAE:  0.10284359392050742
RMSE:  0.12382620797642935
R2:  -0.19607437904147096
MAPE:  inf
Training set size:  210924
8613
49 1

MAE:  0.04135339929804254
RMSE:  0.05973931232265854
R2:  0.5475260188980497
MAPE:  inf

MAE:  0.04161303676236484
RMSE:  0.06048367023887719
R2:  0.5361800266585672
MAPE:  inf
Training set size:  259884
13861
14

12644
1 1

MAE:  0.0335593045438695
RMSE:  0.044071014709703926
R2:  0.4984410376156154
MAPE:  inf

MAE:  0.03340868707367012
RMSE:  0.04084954489867853
R2:  0.5690862619381953
MAPE:  inf
Training set size:  407376
23458
1 2

MAE:  0.01913363427652291
RMSE:  0.025033544756170575
R2:  0.4933064054196684
MAPE:  inf

MAE:  0.015096787932416757
RMSE:  0.021033703524168727
R2:  0.6422890702737956
MAPE:  inf
Training set size:  416376
5444
120 2

MAE:  0.05448655082284078
RMSE:  0.08282139506053647
R2:  0.3789480353141298
MAPE:  inf

MAE:  0.08402568142022047
RMSE:  0.09377913520847118
R2:  0.20373925858269293
MAPE:  inf
Training set size:  395136
6689
120 1

MAE:  0.04174508366528884
RMSE:  0.0666876600281623
R2:  0.3964387119118996
MAPE:  inf

MAE:  0.051893980681533315
RMSE:  0.06107802894372358
R2:  0.4937087220252053
MAPE:  inf
Training set size:  389988
8546
59 1

MAE:  0.01494827499364655
RMSE:  0.02704128867899829
R2:  0.2743005966195853
MAPE:  21.079768477548004

MAE:  0.04632637171

33A 2

MAE:  0.08130712216170385
RMSE:  0.1069521508195259
R2:  0.7031412206239018
MAPE:  inf

MAE:  0.14027368756962577
RMSE:  0.1621148335917368
R2:  0.31794976695523103
MAPE:  inf
Training set size:  44244
5266
33A 1

MAE:  0.05861250509904691
RMSE:  0.08275036438328094
R2:  0.3195150602016408
MAPE:  inf

MAE:  0.12262248112596492
RMSE:  0.14427926409977096
R2:  -1.0686476559674105
MAPE:  inf
Training set size:  29340
6825
41B 1

MAE:  0.06365357438635551
RMSE:  0.08891791699424313
R2:  0.5529438556386967
MAPE:  inf

MAE:  0.19007850460212716
RMSE:  0.2316095481200287
R2:  -2.0331677248754767
MAPE:  inf
Training set size:  34704
5296
41B 2

MAE:  0.1027775463761905
RMSE:  0.13770953655742282
R2:  0.3442109518261318
MAPE:  42.213904222329724

MAE:  0.20975999567330042
RMSE:  0.2484714735545722
R2:  -1.1349573189865185
MAPE:  92.56384985412423
Training set size:  30312
5550
26 1

MAE:  0.05416105601807412
RMSE:  0.07530310810290651
R2:  0.44550768179104205
MAPE:  25.847282531920207

M

4707
70D 2

MAE:  0.11611073132505474
RMSE:  0.14776127175698836
R2:  0.4580053123885245
MAPE:  43.47589990488385

MAE:  0.32138334332080865
RMSE:  0.35877750202425274
R2:  -2.195392361330401
MAPE:  141.7151754000579
Training set size:  3420
6132
70D 1

MAE:  0.10819602322552821
RMSE:  0.14222437130114585
R2:  0.17402435816735184
MAPE:  inf

MAE:  0.3213513198884634
RMSE:  0.3465965729887775
R2:  -3.905324284560259
MAPE:  inf
Training set size:  4176
6719
32X 1

MAE:  0.12305696150183977
RMSE:  0.15692170877672587
R2:  0.4450587240403703
MAPE:  51.00485635370961

MAE:  0.33505652500459404
RMSE:  0.3735186305971611
R2:  -2.1441662996468227
MAPE:  150.72878794735547
Training set size:  11592
7931
32X 2

MAE:  0.08099625150597299
RMSE:  0.11584813432418077
R2:  0.441664006714405
MAPE:  inf

MAE:  0.38294197254140555
RMSE:  0.40230082427784175
R2:  -5.733166938980503
MAPE:  inf
Training set size:  6480
7590
77X 2

MAE:  0.08503377347756542
RMSE:  0.11268069402523269
R2:  0.5020562403070308

25D 1

MAE:  0.05873435237563643
RMSE:  0.08589514344357278
R2:  0.21371510582623576
MAPE:  30.31514205887682

MAE:  0.20039690618092446
RMSE:  0.21670450997909835
R2:  -4.004706497802663
MAPE:  105.3182309107126
Training set size:  18468
6312
15D 2

MAE:  0.11586736958766067
RMSE:  0.15194260013037772
R2:  0.4427129101992022
MAPE:  inf

MAE:  0.20716716533977317
RMSE:  0.2552137322263254
R2:  -0.5722729817937102
MAPE:  inf
Training set size:  4032
5747
15D 1

MAE:  0.08173610690856557
RMSE:  0.10802214554151233
R2:  0.5810237501856622
MAPE:  30.12001554102468

MAE:  0.22772276491511836
RMSE:  0.25936236162567905
R2:  -1.4153368711953709
MAPE:  111.13819893683568
Training set size:  9648
6865
25X 2

MAE:  0.08853811030909421
RMSE:  0.12150842353134114
R2:  0.4576283533883151
MAPE:  inf

MAE:  0.3118321539768928
RMSE:  0.3359586605658884
R2:  -3.1462538480253786
MAPE:  inf
Training set size:  4896
8082
25X 1

MAE:  0.06950691929989772
RMSE:  0.08932834326342816
R2:  0.4330170246619519
M

In [83]:
multiMetrics_mult(models_LR,'test',printall=True) 

9416
66 1

MAE:  0.051544664426776
RMSE:  0.06830706267337577
R2:  0.5671712208163678
MAPE:  16.354612722804056

MAE:  0.09790810558239944
RMSE:  0.11274856703018793
R2:  -0.1792529491095709
MAPE:  35.73951947314073
Training set size:  114048
8648
66 2

MAE:  15403808.177491928
RMSE:  567228371.3647913
R2:  -3.4854414617918247e+19
MAPE:  4238754758.9795732

MAE:  0.05435277724987438
RMSE:  0.06919509929100827
R2:  0.48132827103653375
MAPE:  14.874871736128693
Training set size:  97632
13531
77A 1

MAE:  0.03584220637442719
RMSE:  0.04669817578202679
R2:  0.5792828956251739
MAPE:  10.686980372050721

MAE:  0.04264095477755587
RMSE:  0.0578567514712681
R2:  0.3541994238185312
MAPE:  11.866261310805818
Training set size:  153900
14153
77A 2

MAE:  0.037946773133179686
RMSE:  0.0502706985098506
R2:  0.5368976083774304
MAPE:  18.92554181064786

MAE:  0.08446545961709591
RMSE:  0.09519766455602581
R2:  -0.6607328359148186
MAPE:  47.232160962931424
Training set size:  168264
13579
41 2

MAE: 

7 2

MAE:  2852124.826021142
RMSE:  107721999.80865526
R2:  -6.15153745549069e+17
MAPE:  inf

MAE:  0.06396179766808306
RMSE:  0.08517656827690956
R2:  0.6153948146163548
MAPE:  inf
Training set size:  102708
11861
7 1

MAE:  0.056031144273829755
RMSE:  0.0804913088127245
R2:  0.38899850739705655
MAPE:  29.570126366382144

MAE:  0.1082873585349119
RMSE:  0.12781856768980662
R2:  -0.5407500340420346
MAPE:  65.39381596419287
Training set size:  90360
9073
29A 2

MAE:  0.0330377500140288
RMSE:  0.044311047943864035
R2:  0.4973480835788213
MAPE:  20.499228175546463

MAE:  0.08330409007283344
RMSE:  0.09124635993407382
R2:  -1.1314463080201564
MAPE:  60.44923506991518
Training set size:  164304
6430
29A 1

MAE:  0.04850988565958735
RMSE:  0.06384289227317634
R2:  0.4997216375886303
MAPE:  25.294939077202137

MAE:  0.1304047204284108
RMSE:  0.14285971872717623
R2:  -1.5049911378984593
MAPE:  77.15559189233325
Training set size:  141120
7195
123 2

MAE:  0.056026898593001494
RMSE:  0.07339201

MAPE:  68.61085957862093
Training set size:  97596
16040
145 2

MAE:  0.03714192871345439
RMSE:  0.049409806297465574
R2:  0.4231364885633896
MAPE:  12.878042342036009

MAE:  0.044369045453038325
RMSE:  0.053357712982486635
R2:  0.32726940432998275
MAPE:  13.04471242399641
Training set size:  288792
12770
145 1

MAE:  0.040558340005224944
RMSE:  0.058433092860398675
R2:  0.3413476417357949
MAPE:  12.80383173436489

MAE:  0.03588802969078285
RMSE:  0.0479653414609787
R2:  0.5561935762994307
MAPE:  9.628240849422651
Training set size:  299232
9314
39A 2

MAE:  0.06311139055236836
RMSE:  0.08228628267933422
R2:  0.4846257294964672
MAPE:  26.770735630181868

MAE:  0.08010626843896407
RMSE:  0.09571421096207544
R2:  0.3026983490371383
MAPE:  31.026728446281332
Training set size:  265176
10935
39A 1

MAE:  0.049626880931467124
RMSE:  0.06627573530595425
R2:  0.5496550740067765
MAPE:  17.525284910920718

MAE:  0.04956727701335702
RMSE:  0.06491269127337561
R2:  0.567988413196192
MAPE:  12.349

MAPE:  inf
Training set size:  123156
9326
42 2

MAE:  0.04244827909583621
RMSE:  0.05808401680250165
R2:  0.45658895350735484
MAPE:  inf

MAE:  0.1074602019689608
RMSE:  0.11721578900922987
R2:  -1.2130305450740364
MAPE:  inf
Training set size:  128880
5144
104 1

MAE:  0.06789581877244469
RMSE:  0.09098723288377923
R2:  0.32910216975584194
MAPE:  20.206024947164952

MAE:  0.11004431783386459
RMSE:  0.12480701722429889
R2:  -0.2623316772440567
MAPE:  37.477659516809396
Training set size:  32508
5286
104 2

MAE:  0.07451354750000215
RMSE:  0.10036334414778635
R2:  0.2088793976990403
MAPE:  31.330016618787

MAE:  0.15850271925453804
RMSE:  0.17277889127640142
R2:  -1.3446272739749938
MAPE:  76.81195977885078
Training set size:  40932
9768
63 2

MAE:  0.034277922462191475
RMSE:  0.05122710378614629
R2:  0.3152431416192568
MAPE:  14.767157165269138

MAE:  0.036675885302227054
RMSE:  0.055633599663178435
R2:  0.19237248428559905
MAPE:  14.532814008504962
Training set size:  75816
7828
63 1

MAPE:  17.80128285731086
Training set size:  47376
9083
83A 1

MAE:  0.054496547809074515
RMSE:  0.07331732031684306
R2:  0.5294103422603326
MAPE:  inf

MAE:  0.069137752085332
RMSE:  0.08553631730618551
R2:  0.35948352096926595
MAPE:  inf
Training set size:  44496
9752
11 2

MAE:  0.05602512927656713
RMSE:  0.07663424755737147
R2:  0.543189062811072
MAPE:  22.953797563304423

MAE:  0.06885481399750701
RMSE:  0.08471201403658075
R2:  0.44181172101279476
MAPE:  25.804923143330168
Training set size:  138636
11463
11 1

MAE:  0.08367180607207303
RMSE:  0.10262705159894844
R2:  0.3158345167121567
MAPE:  inf

MAE:  0.11591322578624011
RMSE:  0.13703714972975595
R2:  -0.21987151348658007
MAPE:  inf
Training set size:  133596
7071
79 2

MAE:  0.04796424675056132
RMSE:  0.06949255599304266
R2:  0.3167786979843046
MAPE:  24.95904891917028

MAE:  0.09030228346231818
RMSE:  0.1040326399413752
R2:  -0.5311723075774673
MAPE:  54.25799774036214
Training set size:  107316
7557
79 1

MAE:  0.029885894

4398
238 2

MAE:  0.03797516715815231
RMSE:  0.050684126159367925
R2:  0.3725019382430007
MAPE:  18.251018069687472

MAE:  0.04502332538758679
RMSE:  0.06099873356782567
R2:  0.09111256595270223
MAPE:  18.265861743687427
Training set size:  41832
7846
220 1

MAE:  0.084347511699981
RMSE:  0.10654038219290367
R2:  0.3717161740316973
MAPE:  31.367102538585783

MAE:  0.21940464083454833
RMSE:  0.24046288725710813
R2:  -2.200541727626873
MAPE:  91.86712247847714
Training set size:  21708
10881
220 2

MAE:  0.04253968085185703
RMSE:  0.054803150739934615
R2:  0.35731996191638704
MAPE:  18.266859147170358

MAE:  0.11690217195952006
RMSE:  0.13052773312940585
R2:  -2.645770671099135
MAPE:  53.26988861153572
Training set size:  23904
5880
33A 2

MAE:  0.08715965066664927
RMSE:  0.11804906575713649
R2:  0.6499081521613312
MAPE:  211.9899316674192

MAE:  0.13883281924270408
RMSE:  0.16307610789858956
R2:  0.33190601063277947
MAPE:  96.8258579415945
Training set size:  18972
5266
33A 1

MAE:  0.0

33X 2

MAE:  0.05726426590424058
RMSE:  0.08765449862747367
R2:  0.2845787597368572
MAPE:  20.944523843912272

MAE:  0.20244988359497165
RMSE:  0.21610632011104197
R2:  -3.3485888326888995
MAPE:  86.68800533217464
Training set size:  10800
10488
33X 1

MAE:  0.04377735749325235
RMSE:  0.08009203320647282
R2:  0.024044669916563066
MAPE:  20.54523771835324

MAE:  0.17053295578172545
RMSE:  0.18059424575929348
R2:  -3.962026958830881
MAPE:  90.47505649097198
Training set size:  12312
7237
76A 2

MAE:  0.08640249915541255
RMSE:  0.11308597083152937
R2:  0.6128867680789416
MAPE:  28.056587631725442

MAE:  0.17081351900597988
RMSE:  0.19775030243848982
R2:  -0.18373603210847533
MAPE:  80.68931628729939
Training set size:  5616
7800
76A 1

MAE:  0.11654754332617218
RMSE:  0.1452304919739062
R2:  0.2271328292993835
MAPE:  41.85162356273572

MAE:  0.15114618996017792
RMSE:  0.17849337424285228
R2:  -0.16743696924570073
MAPE:  62.82245191628301
Training set size:  5364
10180
7B 2

MAE:  0.077682

R2:  0.05939857508041302
MAPE:  31.392626780512252

MAE:  0.22093794131764233
RMSE:  0.236139846661286
R2:  -4.986703569741947
MAPE:  104.44356784895487
Training set size:  6336
4476
51D 1

MAE:  0.11470597814256779
RMSE:  0.14103901503725527
R2:  0.20766691567820428
MAPE:  34.100274424095794

MAE:  0.3155120489271813
RMSE:  0.34516512825585693
R2:  -3.7455120827853605
MAPE:  114.54850487610678
Training set size:  2340
5129
69X 2

MAE:  0.13016710695747152
RMSE:  0.17568129356646928
R2:  -0.7583800478446836
MAPE:  24.252305283159814

MAE:  0.14777604565087504
RMSE:  0.17282051493491543
R2:  -0.7015796999858555
MAPE:  31.841989499750913
Training set size:  1620
4664
69X 1

MAE:  0.10919363396200053
RMSE:  0.1436229938091763
R2:  0.08820753718838814
MAPE:  29.40271117493023

MAE:  0.23779876689768828
RMSE:  0.27067711035692554
R2:  -2.2385537557958144
MAPE:  75.9201746236551
Training set size:  2556
5667
27X 2

MAE:  0.1155434972428724
RMSE:  0.14449699638226698
R2:  0.38212436276954764


6950
33E 1

MAE:  0.9862877516472629
RMSE:  1.0253555540850632
R2:  -15.987453280058276
MAPE:  167.72162678526885

MAE:  0.2219452271880526
RMSE:  0.2652518112428894
R2:  -0.13683128098280428
MAPE:  50.14684934114106
Training set size:  180
7659
16D 1

MAE:  0.11809284143243091
RMSE:  0.16826955437439453
R2:  -0.026719816943107322
MAPE:  31.778211216014864

MAE:  0.2766860626336219
RMSE:  0.3095558883512731
R2:  -2.4747134426493007
MAPE:  178.2336084745146
Training set size:  828
4228
41D 1

MAE:  0.18388830396745287
RMSE:  0.21306386743416525
R2:  -2.4791326827043667
MAPE:  24.598233750542448

MAE:  0.2564153851695823
RMSE:  0.28070801577543064
R2:  -5.038944086492581
MAPE:  40.735205594972214
Training set size:  72
4846
41D 2

MAE:  0.6119793065475547
RMSE:  0.696414145342188
R2:  -1.370479817952222
MAPE:  inf

MAE:  0.3405614808282314
RMSE:  0.3865647525442495
R2:  0.26962550585575584
MAPE:  inf
Training set size:  108

Average model RMSE:  344058578966.81067
Average timetable RMSE:

In [84]:
time1 = time.time()

models_KNR = pool_process(mult_funcs.gen_KNR_mult,dfs2_list,4)

print()
print("Seconds taken: ", time.time()-time1)

No. Inputs: 252, pool_size: 4

Seconds taken:  16.882599592208862


In [85]:
multiMetrics_mult(models_KNR,'train') 

9416
8648
13531
14153
13579
9445
11430
8640
11027
6252
10181
14277
10201
8344
10188
13978
12552
12222
10323
10792
9422
10415
10804
11737
8858
10319
9224
10271
8395
12507
7620
11861
9073
6430
7195
8675
11668
13502
12888
9779
8660
7728
9270
10253
12335
12957
17375
10031
12815
11879
12138
14325
7332
12041
9912
16262
13215
9855
9224
7589
11321
4854
16040
12770
9314
10935
9600
8681
6160
6253
6356
6379
6540
6543
10651
10236
9189
8450
7647
7392
16011
8616
10385
9652
9464
8442
16083
9400
6873
6871
9112
9326
5144
5286
9768
7828
10100
7625
9548
16871
10955
7503
8865
8613
13861
13655
9911
10014
4817
5815
10267
10002
4145
9748
6204
6239
7341
8493
9444
7604
9662
9083
9752
11463
7071
7557
6589
6952
12644
23458
5444
6689
8546
3517
9862
9864
10278
6612
9995
10226
12122
9885
7596
7970
11008
8867
4787
7051
8947
5755
7007
8411
4552
9007
7893
6457
7816
4398
7846
10881
5880
5266
6825
5296
5550
6068
6216
5647
3726
5810
5916
5158
9814
7397
7379
7128
8830
7979
6499
6659
10569
7786
5691
10783
8848
10488
7237
7

In [86]:
multiMetrics_mult(models_KNR,'test') 

9416
8648
13531
14153
13579
9445
11430
8640
11027
6252
10181
14277
10201
8344
10188
13978
12552
12222
10323
10792
9422
10415
10804
11737
8858
10319
9224
10271
8395
12507
7620
11861
9073
6430
7195
8675
11668
13502
12888
9779
8660
7728
9270
10253
12335
12957
17375
10031
12815
11879
12138
14325
7332
12041
9912
16262
13215
9855
9224
7589
11321
4854
16040
12770
9314
10935
9600
8681
6160
6253
6356
6379
6540
6543
10651
10236
9189
8450
7647
7392
16011
8616
10385
9652
9464
8442
16083
9400
6873
6871
9112
9326
5144
5286
9768
7828
10100
7625
9548
16871
10955
7503
8865
8613
13861
13655
9911
10014
4817
5815
10267
10002
4145
9748
6204
6239
7341
8493
9444
7604
9662
9083
9752
11463
7071
7557
6589
6952
12644
23458
5444
6689
8546
3517
9862
9864
10278
6612
9995
10226
12122
9885
7596
7970
11008
8867
4787
7051
8947
5755
7007
8411
4552
9007
7893
6457
7816
4398
7846
10881
5880
5266
6825
5296
5550
6068
6216
5647
3726
5810
5916
5158
9814
7397
7379
7128
8830
7979
6499
6659
10569
7786
5691
10783
8848
10488
7237
7

### Improvements with KNN models?

In [87]:
def gen_KNR(df,n_neighbors=5,verbose=False):
    import pandas as pd
    from sklearn.model_selection import train_test_split
    from sklearn.neural_network import MLPRegressor
    from sklearn.svm import SVR
    from sklearn.linear_model import LinearRegression
    from sklearn.neighbors import KNeighborsRegressor

    route = df['LINEID'].unique()[0]
    direction = df['DIRECTION'].unique()[0]
    max_trip = df['TRIPLENGTH'].max()
    
    print(df['TRIPLENGTH'].min(),df['TRIPLENGTH'].max())
    
#     df['TRIPLENGTH'] = (df['TRIPLENGTH'] - df['TRIPLENGTH'].min())/(df['TRIPLENGTH'].max() - df['TRIPLENGTH'].min())
#     df['feels_like'] = (df['feels_like'] - df['feels_like'].min())/(df['feels_like'].max() - df['feels_like'].min())
    
    df_rev1 = pd.get_dummies(df.drop(['LINEID','DIRECTION'],axis=1))
        
#   print(route, direction)
    # y is the target
    y = (df_rev1['TRIPLENGTH'] - df_rev1['TRIPLENGTH'].min())/(df_rev1['TRIPLENGTH'].max() - df_rev1['TRIPLENGTH'].min())
    # X is everything else
    X = df_rev1.drop(["TRIPLENGTH"],1)
    X['feels_like'] = (X['feels_like'] - X['feels_like'].min())/(X['feels_like'].max() - X['feels_like'].min())
    # Split the dataset into two datasets: 70% training and 30% test
    X_train, X_test, y_train, y_test = train_test_split(X, y, random_state=1,  test_size=0.3)

#   timetabled_values_train = X_train['PLANNEDTIME_ARR'] - X_train['PLANNEDTIME_DEP']
#   timetabled_values_test = X_test['PLANNEDTIME_ARR'] - X_test['PLANNEDTIME_DEP']
            
#   X_train.drop('PLANNEDTIME_ARR',axis=1,inplace=True)
#   X_test.drop('PLANNEDTIME_ARR',axis=1,inplace=True)
#   X_train.drop('PLANNEDTIME_DEP',axis=1,inplace=True)
#   X_test.drop('PLANNEDTIME_DEP',axis=1,inplace=True)
            
#   print("original range is: ",df_rev1.shape[0])
#   print("training range (70%):\t rows 0 to", round(X_train.shape[0]))
#   print("test range (30%): \t rows", round(X_train.shape[0]), "to", round(X_train.shape[0]) + X_test.shape[0])
            
# need to reset the index to allow contatenation with predicted values otherwise not joining on same index...
    X_train.reset_index(drop=True, inplace=True)
    y_train.reset_index(drop=True, inplace=True)
    X_test.reset_index(drop=True, inplace=True)
    y_test.reset_index(drop=True, inplace=True)
    X_train.head(5)
        
    timetabled_values_train = X_train['PLANNEDTIME_ARR'] - X_train['PLANNEDTIME_DEP']
    timetabled_values_test = X_test['PLANNEDTIME_ARR'] - X_test['PLANNEDTIME_DEP']
    X_train.drop('PLANNEDTIME_ARR',axis=1,inplace=True)
    X_test.drop('PLANNEDTIME_ARR',axis=1,inplace=True)
    X_train.drop('PLANNEDTIME_DEP',axis=1,inplace=True)
    X_test.drop('PLANNEDTIME_DEP',axis=1,inplace=True)
    
    output_model = KNeighborsRegressor(n_neighbors=n_neighbors).fit(X_train,y_train)
    
#     test_train_dict[key] = {
#                 'X_train':X_train,
#                 'X_test':X_test,
#                 'y_train':y_train,
#                 'y_test':y_test,
#                 'timetabled_values_train':timetabled_values_train,
#                 'timetabled_values_test':timetabled_values_test
#             }
    
    
    output = {
        'route':route,
        'direction':direction,
        'model':output_model,
        'X_train':X_train,
        'X_test':X_test,
        'y_train':y_train,
        'y_test':y_test,
        'timetabled_values_train':timetabled_values_train/max_trip,
        'timetabled_values_test':timetabled_values_test/max_trip,
        'max_trip':max_trip
    }
    if verbose == True:
        print('Done: \t%s\t%s'%(route,direction))
    return output

In [88]:
warnings.filterwarnings('ignore')

time1 = time.time()

models_KNR = []
for df in dfs2_list:
    models_KNR += [gen_KNR(df,n_neighbors=8,verbose=True)]

print()
print("Seconds taken: ", time.time()-time1)

1799 9416
Done: 	66	1
1001 8648
Done: 	66	2
118 13531
Done: 	77A	1
1877 14153
Done: 	77A	2
1377 13579
Done: 	41	2
544 9445
Done: 	41	1
1078 11430
Done: 	83	1
880 8640
Done: 	83	2
371 11027
Done: 	130	2
579 6252
Done: 	130	1
804 10181
Done: 	40	1
741 14277
Done: 	40	2
371 10201
Done: 	151	2
518 8344
Done: 	151	1
945 10188
Done: 	13	1
431 13978
Done: 	13	2
20 12552
Done: 	75	1
1762 12222
Done: 	75	2
1251 10323
Done: 	65	1
2435 10792
Done: 	65	2
914 9422
Done: 	122	2
596 10415
Done: 	122	1
971 10804
Done: 	33	2
2618 11737
Done: 	33	1
51 8858
Done: 	41C	1
447 10319
Done: 	41C	2
897 9224
Done: 	7A	1
1846 10271
Done: 	7A	2
68 8395
Done: 	67	2
2450 12507
Done: 	67	1
585 7620
Done: 	7	2
2301 11861
Done: 	7	1
1101 9073
Done: 	29A	2
1277 6430
Done: 	29A	1
518 7195
Done: 	123	2
1007 8675
Done: 	123	1
1268 11668
Done: 	27	2
1116 13502
Done: 	27	1
805 12888
Done: 	16	1
2599 9779
Done: 	16	2
126 8660
Done: 	150	1
1226 7728
Done: 	150	2
40 9270
Done: 	4	1
303 10253
Done: 	4	2
1017 12335
Done: 	15	1
1

In [89]:
models_KNR[0]

{'route': '66',
 'direction': 1,
 'model': KNeighborsRegressor(algorithm='auto', leaf_size=30, metric='minkowski',
                     metric_params=None, n_jobs=None, n_neighbors=8, p=2,
                     weights='uniform'),
 'X_train':       PLANNEDTIME_DEP_COS  PLANNEDTIME_DEP_SIN  feels_like  MONTH_1  MONTH_2  \
 0               -0.537300             0.843391    0.235018        0        0   
 1                0.831470            -0.555570    0.690464        0        0   
 2               -0.980785             0.195090    0.309536        0        0   
 3               -0.173648             0.984808    0.280875        0        0   
 4               -0.751840             0.659346    0.699062        0        0   
 ...                   ...                  ...         ...      ...      ...   
 7386            -0.043619             0.999048    0.383273        0        0   
 7387            -0.422618             0.906308    0.558885        0        0   
 7388            -0.751840    

In [90]:
multiMetrics_mult(models_KNR,'test') 

KeyError: 'min_trip'

In [ ]:
warnings.filterwarnings('ignore')

time1 = time.time()

models_KNR = []
for df in dfs2_list:
    models_KNR += [gen_KNR(df,n_neighbors=20,verbose=True)]

print()
print("Seconds taken: ", time.time()-time1)

In [ ]:
multiMetrics_mult(models_KNR,'test') 

In [ ]:
warnings.filterwarnings('ignore')

time1 = time.time()

models_KNR = []
for df in dfs2_list:
    models_KNR += [gen_KNR(df,n_neighbors=30,verbose=True)]

print()
print("Seconds taken: ", time.time()-time1)

In [ ]:
multiMetrics_mult(models_KNR,'test') 

In [ ]:
warnings.filterwarnings('ignore')

time1 = time.time()

models_KNR = []
for df in dfs2_list:
    models_KNR += [gen_KNR(df,n_neighbors=50,verbose=True)]

print()
print("Seconds taken: ", time.time()-time1)

In [ ]:
multiMetrics_mult(models_KNR,'test') 

### KNN with large number of neighbours is waaaaaay too slow

In [ ]:
import xgboost as xgb

In [ ]:
def gen_xgb(df,verbose=False):
    import pandas as pd
    from sklearn.model_selection import train_test_split
    from sklearn.neural_network import MLPRegressor
    from sklearn.svm import SVR
    from sklearn.linear_model import LinearRegression
    from sklearn.neighbors import KNeighborsRegressor

    route = df['LINEID'].unique()[0]
    direction = df['DIRECTION'].unique()[0]
    max_trip = df['TRIPLENGTH'].max()
    
    print(df['TRIPLENGTH'].min(),df['TRIPLENGTH'].max())
    
#     df['TRIPLENGTH'] = (df['TRIPLENGTH'] - df['TRIPLENGTH'].min())/(df['TRIPLENGTH'].max() - df['TRIPLENGTH'].min())
#     df['feels_like'] = (df['feels_like'] - df['feels_like'].min())/(df['feels_like'].max() - df['feels_like'].min())
    
    df_rev1 = pd.get_dummies(df.drop(['LINEID','DIRECTION'],axis=1))
        
#   print(route, direction)
    # y is the target
    y = (df_rev1['TRIPLENGTH'] - df_rev1['TRIPLENGTH'].min())/(df_rev1['TRIPLENGTH'].max() - df_rev1['TRIPLENGTH'].min())
    # X is everything else
    X = df_rev1.drop(["TRIPLENGTH"],1)
    X['feels_like'] = (X['feels_like'] - X['feels_like'].min())/(X['feels_like'].max() - X['feels_like'].min())
    # Split the dataset into two datasets: 70% training and 30% test
    X_train, X_test, y_train, y_test = train_test_split(X, y, random_state=1,  test_size=0.3)

#   timetabled_values_train = X_train['PLANNEDTIME_ARR'] - X_train['PLANNEDTIME_DEP']
#   timetabled_values_test = X_test['PLANNEDTIME_ARR'] - X_test['PLANNEDTIME_DEP']
            
#   X_train.drop('PLANNEDTIME_ARR',axis=1,inplace=True)
#   X_test.drop('PLANNEDTIME_ARR',axis=1,inplace=True)
#   X_train.drop('PLANNEDTIME_DEP',axis=1,inplace=True)
#   X_test.drop('PLANNEDTIME_DEP',axis=1,inplace=True)
            
#   print("original range is: ",df_rev1.shape[0])
#   print("training range (70%):\t rows 0 to", round(X_train.shape[0]))
#   print("test range (30%): \t rows", round(X_train.shape[0]), "to", round(X_train.shape[0]) + X_test.shape[0])
            
# need to reset the index to allow contatenation with predicted values otherwise not joining on same index...
    X_train.reset_index(drop=True, inplace=True)
    y_train.reset_index(drop=True, inplace=True)
    X_test.reset_index(drop=True, inplace=True)
    y_test.reset_index(drop=True, inplace=True)
    X_train.head(5)
        
    timetabled_values_train = X_train['PLANNEDTIME_ARR'] - X_train['PLANNEDTIME_DEP']
    timetabled_values_test = X_test['PLANNEDTIME_ARR'] - X_test['PLANNEDTIME_DEP']
    X_train.drop('PLANNEDTIME_ARR',axis=1,inplace=True)
    X_test.drop('PLANNEDTIME_ARR',axis=1,inplace=True)
    X_train.drop('PLANNEDTIME_DEP',axis=1,inplace=True)
    X_test.drop('PLANNEDTIME_DEP',axis=1,inplace=True)
    
    D_train = xgb.DMatrix(X_train, label=y_train)
    D_test = xgb.DMatrix(X_test, label=y_test)
    
    param = {
    'eta': 0.3, 
    'objective': 'reg:squaredlogerror',
    'max_depth':20
    } 

    steps = 20  # The number of training iterations

    
    output_model = xgb.train(param, D_train, steps)

    
#     test_train_dict[key] = {
#                 'X_train':X_train,
#                 'X_test':X_test,
#                 'y_train':y_train,
#                 'y_test':y_test,
#                 'timetabled_values_train':timetabled_values_train,
#                 'timetabled_values_test':timetabled_values_test
#             }
    
    
    output = {
        'route':route,
        'direction':direction,
        'model':output_model,
        'D_test':D_test,
        'D_train':D_train,
        'X_train':X_train,
        'X_test':X_test,
        'y_train':y_train,
        'y_test':y_test,
        'timetabled_values_train':timetabled_values_train/max_trip,
        'timetabled_values_test':timetabled_values_test/max_trip,
        'max_trip':max_trip
    }
    if verbose == True:
        print('Done: \t%s\t%s'%(route,direction))
    return output

In [ ]:
warnings.filterwarnings('ignore')

time1 = time.time()

models_xgb = []
for df in dfs2_list:
    models_xgb += [gen_xgb(df,verbose=True)]

print()
print("Seconds taken: ", time.time()-time1)

In [ ]:
models_xgb

In [ ]:
def xgb_Metrics(models):
    import numpy as np
    from sklearn.metrics import precision_score, recall_score, accuracy_score
    for model in models:
        y_test = model['y_test']
        preds = model['model'].predict(model['D_test'])
        best_preds = np.asarray([np.argmax(line) for line in preds])
        print(model['route'] + " - " + str(model['direction']))
        print('---')
        print('RMSE = {}'.format(metrics.mean_squared_error(y_test,best_preds)))
#         print("Precision = {}".format(precision_score(y_test, best_preds, average='macro')))
#         print("Recall = {}".format(recall_score(y_test, best_preds, average='macro')))
#         print("Accuracy = {}".format(accuracy_score(y_test, best_preds)))
        print()

In [ ]:
xgb_Metrics(models_xgb)

In [ ]:
models_xgb[0]['D_test']

In [98]:
dftrips_fresh = pd.read_csv('../../data/rt_trips_DB_2018.txt',sep=';')

dftrips_fresh.head()

DATASOURCE        DAYOFSERVICE   TRIPID LINEID  ROUTEID  DIRECTION  \
0         DB  07-FEB-18 00:00:00  6253783     68    68_80          1   
1         DB  07-FEB-18 00:00:00  6262138    25B  25B_271          2   
2         DB  07-FEB-18 00:00:00  6254942    45A   45A_70          2   
3         DB  07-FEB-18 00:00:00  6259460    25A  25A_273          1   
4         DB  07-FEB-18 00:00:00  6253175     14    14_15          1   

   PLANNEDTIME_ARR  PLANNEDTIME_DEP  ACTUALTIME_ARR  ACTUALTIME_DEP   BASIN  \
0            87245            84600         87524.0         84600.0  BasDef   
1            30517            26460         32752.0             NaN  BasDef   
2            35512            32100         36329.0         32082.0  BasDef   
3            57261            54420         58463.0         54443.0  BasDef   
4            85383            81600         84682.0         81608.0  BasDef   

   TENDERLOT  SUPPRESSED  JUSTIFICATIONID          LASTUPDATE       NOTE  
0        NaN         NaN              NaN  28-FEB-18 12:05:11  ,2967409,  
1        NaN         NaN              NaN  28-FEB-18 12:05:11  ,2580260,  
2        NaN         NaN              NaN  28-FEB-18 12:05:11  ,2448968,  
3        NaN         NaN              NaN  28-FEB-18 12:05:11  ,3094242,  
4        NaN         NaN              NaN  28-FEB-18 12:05:11  ,2526331,

In [105]:
dftrips_fresh[dftrips_fresh['LINEID'] == '46A'][dftrips_fresh['DIRECTION'] == 1]['PLANNEDTIME_DEP'].unique()

array([60960, 24480, 83700, 77400, 75600, 74700, 80100, 76500, 79200,
       82800, 81900, 81000, 78300, 25740, 69600, 66240, 63360, 65760,
       62280, 64320, 64800, 63840, 26400, 29760, 28800, 30240, 28320,
       27840, 24000, 55200, 56160, 60780, 59520, 62880, 61440, 62400,
       70200, 46080, 26880, 81600, 73800, 47400, 54000, 53400, 54600,
       52800, 57600, 59040, 57120, 58560, 58080, 84600, 58140, 45720,
       34200, 31800, 33000, 30600, 61200, 53280, 54240, 48960, 33300,
       35460, 50400, 66600, 66000, 65400, 64200, 48600, 29280, 27360,
       66720, 72000, 69000, 73200, 70800, 72600, 21960, 71400, 36000,
       55800, 31200, 33600, 32640, 32160, 33120, 31680, 30720, 34080,
       18900, 72900, 41400, 29520, 28980, 27900, 28440, 30060, 52200,
       43200, 36900, 40500, 35100, 42300, 38700, 39600, 44400, 37800,
       45000, 34800, 45600, 46800, 49200, 46200, 48000, 51000, 49800,
       51600, 67800, 69300, 67200, 68400, 59400, 40200, 58200, 49920,
       46560, 49440,